# DATA CLEANING

### 1. PULIZIA PER VALIDITÀ ATTIVITÀ
### 2. SELEZIONO SOLO SAGGI SU MMP9 E SU VERSIONE UMANA
### (RIMOZIONE VALORI ATTIVITÀ NULLA)
### 3. PULIZIA IN BASE ALLA RELAZIONE CON ATTIVITÀ
### 4. SELEZIONE TIPO ATTIVITÀ
### 5. CONVERSIONE IN pAct
### 6.SELEZIONE TIPO DI SAGGIO B
### 7.VISUALIZZAZIONE DI TUTTI I DUPLICATI
### 8. ANALISI DUPLICATI CHIRALI
### 9. Controllo dei duplicati non chirali
### 10. UNIONE DUPLICATI CHIRALI E NON¶
### 11. UNIONE COMPOSTI UNICI CON DUPLICATI
### 12. LEVARE GLI IONI DEI SALI
### 13. SELEZIONE PER PESO MOLECOLARE

In [1]:
#allargamento display ed importazione librerie di interesse
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>")) 
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import pickle
import matplotlib.pyplot as plt
%matplotlib inline
import copy
import glob
import io

/tmp/ipykernel_574748/2182679113.py:2: DeprecationWarning: Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython display
  from IPython.core.display import display, HTML


In [2]:
#from myutilities import (prepare_bindingdb_dataframe, prepare_chembl_dataframe, prepare_pubchem_dataframe)
from rdkit import Chem
from rdkit.Chem import AllChem
from rdkit.Chem import Descriptors
from rdkit.Chem import PandasTools
from rdkit.Chem.Draw import IPythonConsole
#from rdkit.Chem import Draw

In [3]:
std_type = 'IC50'
purpose = 'CLASSIFICATION'

In [4]:
imported = pickle.load(open('/home/robertastolfi/HDAC/HDAC1/Selezione_dati_attivita.pickle', 'rb'))

In [5]:
imported.shape

(8363, 10)

In [6]:
imported.isna().any()#mi assicuro che non ci siano nan

ID                     False
ISOMERIC SMILES        False
STANDARD TYPE          False
STANDARD RELATION      False
STANDARD VALUE         False
STANDARD UNITS         False
 ASSAY TYPE            False
MW                     False
STANDARD VALUE [nM]    False
pAct                   False
dtype: bool

In [7]:
df_chembl = imported

# Visualizzazione - analisi - rimozione duplicati
### VISUALIZZAZIONE: 
calcolo INCHI derivato da CANONICAL SMILES (non ci sono informazioni sulla stereoisomeria) e successivo confronto dei duplicati solo tramite INCHI
### ANALISI: la stereoisomeria ha peso sull’attività?
-tra i duplicati, ci sono stereoisomeri? SÌ
-hanno valori di attività diverse? NO
-i diversi valori di attività NON sono da imputare alla diversa stereoisomeria
### RIMOZIONE:
stesso flusso del nb precedente: media - deviazione std - selezione records con std dev minore di 1

## 7. LEVARE GLI IONI DEI SALI
Sfrutto il fatto che sono separati dal punto e che il massimo di lunghezza della stringa per lo ione è 5 perchè si può trovare tra parentesi quadre con la carica

In [8]:
#eliminazione 'nan' dalla colonna ['ISOMERIC SMILES']
df_chembl = df_chembl[df_chembl['ISOMERIC SMILES'].notnull()].copy() #mi assicuro che ci siano tutte le smiles
df_chembl['ISOMERIC SMILES']  

0             COc1ccc(NC(=O)Nc2ccc(/C=C/C(=O)NO)cc2)cc1OC
1       Cc1ccc(NS(=O)(=O)c2ccc(/C=C/C(=O)Nc3ccccc3N)cc...
2               Nc1ccccc1NC(=O)CCCCCNS(=O)(=O)c1ccc(F)cc1
3                     Nc1ccccc1NC(=O)CCCCCNC(=O)c1ccccc1F
4             Nc1ccccc1NC(=O)CCCCCn1c(=O)[nH]c2ccccc2c1=O
5        CC(/C=C/C(=O)NO)=C\[C@@H](C)C(=O)c1ccc(N(C)C)cc1
6       COc1cc([C@@H]2c3cc4c(cc3[C@@H](Nc3ccccc3OCCCCC...
7       COc1cc([C@@H]2c3cc4c(cc3[C@@H](Nc3ccc(OCCCCC(=...
8       COc1cc([C@@H]2c3cc4c(cc3[C@@H](Nc3cccc(OCCCC(=...
9       COc1cc([C@@H]2c3cc4c(cc3[C@@H](Nc3ccc(NC(=O)CC...
10                         Cc1cccc(NC(=O)CCCCCCC(=O)NO)c1
11      O=C(CCCCC[C@H](NC(=O)[C@@H]1CC(=O)N1)C(=O)Nc1c...
12                  COc1ccc(NC(=O)NCc2ccc(C(=O)NO)cc2)cc1
13      CC(Cc1nc2cc(/C=C/C(=O)NO)ccc2n1CC(C)(C)CN(C)C)...
14      CCC(=O)CCCCC[C@H](NC(=O)[C@H]1CC12CCN(C)CC2)c1...
15      CCC(=O)CCCCC[C@H](NC(=O)[C@H]1CC12CCN(CC)CC2)c...
16      CCC(=O)CCCCC[C@H](NC(=O)c1ccon1)c1[nH]c(-c2ccc...
17      CCC(=O

In [9]:
df_chembl = df_chembl.reset_index(drop=True)

In [10]:
df_chembl.index

RangeIndex(start=0, stop=8363, step=1)

In [16]:
smi_Si =[]
for smi in df_chembl['ISOMERIC SMILES']:
    if 'Si' in smi:
        smi_Si.append(smi)

In [17]:
smi_Si

['Cc1cn([C@H]2C[C@H](C3(c4ccc(NC(=O)CCCCCCC(=O)NO)cc4)SCCCS3)[C@@H](CO[Si](C)(C)C(C)(C)C)O2)c(=O)[nH]c1=O',
 'Cc1cn([C@@H]2C[C@H](C3(c4ccc(NC(=O)CCCCCC(=O)NO)cc4)SCCCS3)[C@@H](CO[Si](C)(C)C(C)(C)C)O2)c(=O)[nH]c1=O',
 'CC(/C=C/C(=O)NO)=C\\C(C)C(=O)c1ccc(C2([C@H]3CC(=O)O[C@@H]3CO[Si](C)(C)C(C)(C)C)SCCCS2)cc1',
 'Cc1cn([C@@H]2C[C@H](C3(c4ccc(NC(=O)CCCCCCC(=O)NO)cc4)SCCCS3)[C@@H](CO[Si](C)(C)C(C)(C)C)O2)c(=O)[nH]c1=O',
 'C#Cc1ccc(CNC(=O)O[C@H]2C[C@@H](C)C=C3C=C[C@H](C)[C@H](CC[C@@H]4C[C@@H](O[Si](C)(C)C(C)(C)C)CC(=O)O4)[C@H]32)cc1',
 'Cc1cn([C@@H]2C[C@H](C3(c4ccc(NC(=O)CCCCC(=O)NO)cc4)SCCCS3)[C@@H](CO[Si](C)(C)C(C)(C)C)O2)c(=O)[nH]c1=O',
 'Cc1cn([C@H]2C[C@H](C3(c4ccc(NC(=O)CCCCCC(=O)NO)cc4)SCCCS3)[C@@H](CO[Si](C)(C)C(C)(C)C)O2)c(=O)[nH]c1=O',
 'Cc1cn([C@H]2C[C@H](C3(c4ccc(NC(=O)CCCCC(=O)NO)cc4)SCCCS3)[C@@H](CO[Si](C)(C)C(C)(C)C)O2)c(=O)[nH]c1=O',
 'COc1ccc(C2([C@H]3C[C@H](n4cc(C)c(=O)[nH]c4=O)O[C@@H]3CO[Si](C)(C)C(C)(C)C)SCCCS2)cc1OC',
 'C#Cc1ccc(NC(=O)O[C@H]2C[C@@H](C)C=C3C=C[C@H](C)[C@H]

In [18]:
df_chembl = df_chembl[~df_chembl['ISOMERIC SMILES'].isin(smi_Si)]

In [19]:
df_chembl = df_chembl.reset_index(drop=True)

In [20]:
df_chembl.index

RangeIndex(start=0, stop=8345, step=1)

In [21]:
smi_list = []
for smi in df_chembl['ISOMERIC SMILES']:
    if '.' in smi:
        print(smi)
        components = smi.split('.')
        
        mol_list = [comp for comp in components if len(comp) > 5] #in questo modo faccio una lista solo con una smile con lunghezza maggiore di cinque scarto ioni positivi Es:[Li+]
        #print(mol_list)
        mol = mol_list[0]
        print(mol)
        smi_list.append(mol)
        #print(smi)
        #print(components)
    else: 
        mol = smi
        smi_list.append(mol)

Cl.O=C(O)CCP(CCC(=O)O)CCC(=O)O
O=C(O)CCP(CCC(=O)O)CCC(=O)O
Cl.Cn1cc(CN2CC3(CCN(c4ncc(C(=O)NO)cn4)C3)C2)c2ccc(C#N)cc21
Cn1cc(CN2CC3(CCN(c4ncc(C(=O)NO)cn4)C3)C2)c2ccc(C#N)cc21
Cl.O=C(NO)c1ccc(CN2c3ccccc3Sc3ccccc32)nc1
O=C(NO)c1ccc(CN2c3ccccc3Sc3ccccc32)nc1
Cc1[nH]c2ccccc2c1CCNCc1cccc(/C=C/C(=O)NO)c1.Cl
Cc1[nH]c2ccccc2c1CCNCc1cccc(/C=C/C(=O)NO)c1
CCCC(=O)[O-].[Na+]
CCCC(=O)[O-]
CN(C)CCOc1ccc(-c2cc(=O)c3c(O)cc(OCCCCCC(=O)NO)cc3o2)cc1.Cl
CN(C)CCOc1ccc(-c2cc(=O)c3c(O)cc(OCCCCCC(=O)NO)cc3o2)cc1
Cl.NCCCCNCCCCNCCCN1C(=O)c2ccc3c4c(ccc(c24)C1=O)C(=O)N(CCCCCC(=O)NO)C3=O
NCCCCNCCCCNCCCN1C(=O)c2ccc3c4c(ccc(c24)C1=O)C(=O)N(CCCCCC(=O)NO)C3=O
CC(=O)CCCCC[C@H](NC(=O)CCN1CCCCC1)C(=O)Nc1cnc2ccccc2c1.Cl.Cl
CC(=O)CCCCC[C@H](NC(=O)CCN1CCCCC1)C(=O)Nc1cnc2ccccc2c1
CCCCCCN(CCC)NC(=O)/C=C/c1ccc(CNCCc2c(C)[nH]c3ccccc23)cc1.O=C(O)C(F)(F)F
CCCCCCN(CCC)NC(=O)/C=C/c1ccc(CNCCc2c(C)[nH]c3ccccc23)cc1
CCCNNC(=O)/C=C/c1ccc(CNCCc2c(C)[nH]c3ccccc23)cc1.O=C(O)C(F)(F)F
CCCNNC(=O)/C=C/c1ccc(CNCCc2c(C)[nH]c3ccccc23)cc1
Cl.O=C(/

In [22]:
df_chembl.shape, len(smi_list)

((8345, 10), 8345)

In [23]:
 df_chembl['ISOMERIC SMILES'] = smi_list

In [24]:
df_chembl.head()

ID                                    ISOMERIC SMILES  \
0   CHEMBL148769        COc1ccc(NC(=O)Nc2ccc(/C=C/C(=O)NO)cc2)cc1OC   
1   CHEMBL346414  Cc1ccc(NS(=O)(=O)c2ccc(/C=C/C(=O)Nc3ccccc3N)cc...   
2  CHEMBL3916454          Nc1ccccc1NC(=O)CCCCCNS(=O)(=O)c1ccc(F)cc1   
3  CHEMBL3936525                Nc1ccccc1NC(=O)CCCCCNC(=O)c1ccccc1F   
4   CHEMBL327924        Nc1ccccc1NC(=O)CCCCCn1c(=O)[nH]c2ccccc2c1=O   

  STANDARD TYPE STANDARD RELATION  STANDARD VALUE STANDARD UNITS  ASSAY TYPE  \
0          IC50               '='          1000.0             nM           B   
1          IC50               '='          2000.0             nM           B   
2          IC50               '='         24000.0             nM           B   
3          IC50               '='          1135.0             nM           B   
4          IC50               '='          4000.0             nM           B   

           MW  STANDARD VALUE [nM]      pAct  
0  357.132471               1000.0  6.000000  
1  407.130363               2000.0  5.698970  
2  379.136591              24000.0  4.619789  
3  343.169605               1135.0  5.945004  
4  366.169191               4000.0  5.397940

In [25]:
for smi in df_chembl['ISOMERIC SMILES']:
    if '.' in smi:
        print(smi)
#mi assicuro che non ci siano più ioni

In [26]:
df_chembl.index

RangeIndex(start=0, stop=8345, step=1)

# 8. VISUALIZZAZIONE DI TUTTI I DUPLICATI:
calcolo INCHI derivato da CANONICAL SMILES (non ci sono informazioni sulla stereoisomeria) e successivo confronto dei duplicati solo tramite INCHI

In [27]:
import openbabel

In [28]:
from openbabel import pybel

In [29]:
# versione con pybel
# generazione canonical smiles prive di eventuali proprietà stereoisomeriche
canonical_smiles = [] 
for smi in df_chembl['ISOMERIC SMILES'].values:
    pysmi = pybel.readstring('smi', smi).write('can', opt ={'n': True, 'i': True})
    smi = pysmi.replace('\n', '')
    print(smi)
    canonical_smiles.append(smi)

ONC(=O)C=Cc1ccc(cc1)NC(=O)Nc1ccc(c(c1)OC)OC
O=C(Nc1ccccc1N)C=Cc1ccc(cc1)S(=O)(=O)Nc1ccc(cc1)C
O=C(Nc1ccccc1N)CCCCCNS(=O)(=O)c1ccc(cc1)F
O=C(Nc1ccccc1N)CCCCCNC(=O)c1ccccc1F
O=C(Nc1ccccc1N)CCCCCn1c(=O)[nH]c2c(c1=O)cccc2
ONC(=O)C=CC(=CC(C(=O)c1ccc(cc1)N(C)C)C)C
ONC(=O)CCCCCCOc1ccccc1NC1C2COC(=O)C2C(c2c1cc1OCOc1c2)c1cc(OC)c(c(c1)OC)O
ONC(=O)CCCCOc1ccc(cc1)NC1C2COC(=O)C2C(c2c1cc1OCOc1c2)c1cc(OC)c(c(c1)OC)O
ONC(=O)CCCOc1cccc(c1)NC1C2COC(=O)C2C(c2c1cc1OCOc1c2)c1cc(OC)c(c(c1)OC)O
ONC(=O)CCCCCCC(=O)Nc1ccc(cc1)NC1C2COC(=O)C2C(c2c1cc1OCOc1c2)c1cc(OC)c(c(c1)OC)O
ONC(=O)CCCCCCC(=O)Nc1cccc(c1)C
ONC(=O)CCCCCC(C(=O)Nc1ccccc1)NC(=O)C1CC(=O)N1
ONC(=O)c1ccc(cc1)CNC(=O)Nc1ccc(cc1)OC
ONC(=O)C=Cc1ccc2c(c1)nc(n2CC(CN(C)C)(C)C)CC(CC(C)(C)C)C
CCC(=O)CCCCCC(c1[nH]c(nc1C#N)c1ccc2c(c1)cn(n2)C)NC(=O)C1CC21CCN(CC2)C
CCN1CCC2(CC1)CC2C(=O)NC(c1[nH]c(nc1C#N)c1ccc(cc1)F)CCCCCC(=O)CC
CCC(=O)CCCCCC(c1[nH]c(nc1C#N)c1ccc(cc1)F)NC(=O)c1nocc1
CCC(=O)CCCCCC(c1[nH]c(nc1C(=O)N)c1ccc(cc1)F)NC(=O)C1CCOCC1
CCC(=O)CCCCCC(c1[nH]c(nc

COc1ccc2c(c1)c(CC(=O)NC(C(=O)NCCc1c([nH]c3c1cccc3)c1ccccc1)CCCCCC(=O)N)c([nH]2)C
CC(=O)CCCCCC(C(=O)NCCc1c([nH]c2c1cccc2)c1ccccc1)NC(=O)c1cncs1
COc1ccc2c(c1)c(CC(=O)NC(C(=O)Nc1ccccc1)CCCCCC(=O)C)c([nH]2)C
ONC(=O)CCCCCCC(=O)Nc1ccc2c(c1)CCN2C(=O)c1cc(C(C)C)c(cc1O)O
CC(=O)SCCC=CC1CC(=O)NC(C)C(=O)NC(Cc2ccccc2)C(=O)NC(C(=O)NCC(=O)O1)C(C)C
ONC(=O)C=Cc1ccc(cc1)NS(=O)(=O)c1cccc2c1c1ccccc1o2
COc1ccc(cc1)S(=O)(=O)Nc1ccc(cc1)C=CC(=O)Nc1ccccc1N
COC(=O)CCCCN1C(=O)C(CCCNC(=N)NS(=O)(=O)c2c(C)c(C)c3c(c2C)CC(O3)(C)C)N=C(c2c1cccc2)c1ccccc1
COc1ccc(cc1)C(=O)NC(C(=O)NCc1ccc(cc1)C(=O)Nc1ccccc1N)Cc1c[nH]c2c1cccc2
[O-]C(=O)CCC
ONC(=O)CCCCN1C(=O)C(N=C(c2c1cccc2)c1ccccc1)Cc1cnc[nH]1
ONC(=O)C=Cc1ccc(cc1)S(=O)(=O)Nc1ccc(c(c1)OC)OC
COc1ccc(cc1OC)NS(=O)(=O)c1ccc(cc1)C=CC(=O)Nc1ccccc1N
ONC(=O)C=Cc1ccc2n(c1)c(Nc1ccc(cc1)N1CCCCC1)c(n2)CCc1ccccc1
ONC(=O)C=Cc1ccc2n(c1)c(Nc1ccc3c(c1)OCO3)c(n2)CCc1ccccc1
COCCNc1c(CCC(=O)O)nc2n1cc(C=CC(=O)NO)cc2
ONC(=O)C=Cc1ccc2n(c1)c(NC(C)C)c(n2)C(C)C
CCCCCCc1nc2n(c1NCCC(=O)NCC)cc(cc2)C=C

O=C(C=Cc1cnc2n1nccc2)NCCc1ccc(cc1)C(=O)Nc1ccccc1N
O=C(Nc1ccccc1N)CCCCCNc1nn2c(c3c1cccc3)nc1c(c2=O)cc(cc1)Br
ONC(=O)CCCCCNc1nn2c(c3c1cccc3)nc1c(c2=O)cc(cc1)Br
ONC(=O)COc1ccc(cc1)N(c1ncnc2c1cccc2)C
ONC(=O)CCCN1CCN(CC1)c1ccc(cn1)c1cc(C(=O)NCc2c(C)cc([nH]c2=O)C)c2c(c1)n(nc2)C(C)C
ONC(=O)CCCCCCNC(=O)c1cnc(s1)c1ccc(cc1)NC(=O)OC(C)(C)C
COc1cc(cc(c1OC)OC)c1ncc(s1)C=CC(=O)Nc1ccccc1N
ONC(=O)c1ccc(c(c1)F)CN(C(=O)c1ccccc1C(C)C)CC(=O)NC(C)(C)C
CCCCCCCC(=O)SCCC=CC1CC(=O)NCc2occ(n2)C2=NC(C(=O)NC(C(=O)O1)C(C)C)(C)CS2
O=C1NCc2occ(n2)C2=NC(C(=O)NC(C(=O)OC(C1)C=CCCSSCCC=CC1CC(=O)NCc3occ(n3)C3=NC(C(=O)NC(C(=O)O1)C(C)C)(C)CS3)C(C)C)(CS2)C
CC(=O)SCCCCCCn1cc(c2c1cccc2)C(=O)NC1C2CC3CC1CC(C2)C3
ONC(=O)CCCCCCn1cc(c2c1cccc2)C(=O)Nc1ccc(cc1Cl)Cl
COc1ccc(cc1)NC(=O)CNCCCC(=O)Nc1ccccc1N
O=C(NC(C(=O)OCc1ccc(cc1)c1ccccc1)CCCCCCSSc1ccccn1)OCc1ccccc1
O=C(NC(C(=O)NC1c2ccccc2-c2c1cccc2)CCCCCCSSc1ccccn1)OCc1ccccc1
O=C(Nc1ccc(cc1)C)CNCCCC(=O)Nc1ccccc1N
[N-]=[N+]=Nc1cc(CN=[N+]=[N-])cc(c1)C(=O)Nc1ccc(cc1)c1onc(c1)C(=O)NCCCCCC

ONC(=O)CCCCCC(=O)Nc1ccc(cc1)c1scc(n1)C(=O)c1cc(OC)c(c(c1)OC)OC
COc1ccc2c(c1)c(CC(=O)NC(c1ncc([nH]1)c1ccccc1)CCCCCC(=O)C)c([nH]2)C
COc1ccc2c(c1)c(CC(=O)NC(c1ncc([nH]1)c1ccc3c(c1)cccc3)CCCCCC(=O)O)c([nH]2)C
OC(=O)CCCCCC(c1ncc([nH]1)c1ccc2c(c1)cccc2)NS(=O)(=O)N(C)C
CN1CCC(CC1)C(=O)NC(c1ncc([nH]1)c1ccc2c(c1)cccc2)CCCCCC(=O)O
ONC(=O)C=Cc1cccc(c1)C(C(=O)Nc1ccccc1)C(=O)Nc1ccccc1
CSCCC=CC1CC(=O)CC(C(C)C)C(=O)NC(CSC)C(=O)NC(=CC)C(=O)NC(C(=O)O1)C(C)C
ONC(=O)CCCCCN1C(=NC2C1C(=C(Br)C(=C2Br)Br)Br)N(C)C
CCOP(=O)(Cc1cccc(c1)C(=O)Nc1cc(ccc1N)c1cccs1)OCC
CCN1CCN(CC1)Cc1cc(nc(n1)C)Nc1ncc(s1)C(=O)Nc1ccccc1N
Clc1nc(Cl)c2c(n1)n(cc2)Cc1ccc(cc1)C(=O)Nc1ccccc1N
ONC(=O)Cc1ccc(cc1)NS(=O)(=O)c1ccccc1
O=C(Nc1ccccc1N)C=Cc1cnn(c1)CC=Cc1ccccc1
N#Cc1ccccc1C(=O)NCCCCC(c1ncc([nH]1)c1ccc2c(c1)cccc2)NC(=O)c1scnc1
Cc1ccc(cc1)Nc1nc(Cl)nc2c1ncn2Cc1ccc(cc1)C(=O)Nc1ccccc1N
CCC(=O)CCCCCC(c1ncc(o1)c1cc2ccccc2nc1OC)NC(=O)Cn1nncc1
ONC(=O)c1ccc(cc1)CN1CCN(CC1)C(=O)c1c[nH]c2c1ccc(c2)OCc1ccccc1
ONC(=O)c1ccc(cc1)CN1CCN(CC1)C(=O)c1c[n

ONC(=O)CCCCN1C(=O)C(N=C(c2c1cccc2)c1ccccc1)Cc1cncn1C(c1ccccc1)(c1ccccc1)c1ccccc1
ONC(=O)CCCCN1C(=O)C(CC(=O)O)N=C(c2c1cccc2)c1ccccc1
ONC(=O)CCCCC=C(c1ccccn1)c1ccccn1
ONC(=O)c1cnc(nc1)NCc1ccc(cc1C(F)(F)F)F
ONC(=O)C=Cc1ccc(cc1)NS(=O)(=O)c1ccc(cc1)OC
ONC(=O)CCCCCn1nnc(c1)c1cccc(c1)Nc1c2cc(OC)ccc2nc2c1ccc(c2)Cl
ONC(=O)C=Cc1ccc(cc1)NS(=O)(=O)c1ccc2c(c1)cccc2
ONC(=O)CCCCCCn1nnc(c1)COc1ccc2c(c1)cc1c(-c3n(C1)c(=O)c1c(c3)C(O)(CC)C(=O)OC1)n2
Fc1ccc(c(c1)N)NC(=O)c1ccc(cn1)NC(=O)C(c1ccccc1)C
Fc1ccc(c(c1)NC(=O)c1cnc2c(c1)ccc(c2)N1CCNCC1)N
O=C(C=C1NC(=O)c2c1cccc2)NCc1ccc(cc1)C(=O)Nc1ccccc1N
O=C(C=C1NC(=O)c2c1cccc2)NCCCCCCC(=O)Nc1ccccc1N
O=C(Cc1ccccc1)Nc1ccc(cc1)C(=O)Nc1ccc(cc1N)F
CCC(=O)CCCCCC(c1ncc([nH]1)Cc1ccncc1)Oc1ccc2c(c1)cccc2
ONC(=O)CCCCCCOc1cc(C=CC(=O)c2cc(OC)c(c(c2)OC)OC)ccc1OC
ONC(=O)CCCCCCC(=O)Nc1n[nH]c2c1ccc(c2)c1ccccc1OC
ONC(=O)C1CCC(CC1)C(=O)Nc1n[nH]c2c1ccc(c2)c1cccc(c1)OC
O=C(c1scnc1)NC(c1ncc([nH]1)c1ccc2c(c1)cccc2)CCCCNC(=O)c1c(O)cccc1F
CCC(=O)CCCCCC(c1ncc([nH]1)c1cc2ccc(nc2cc1OC)N1CC

SCC(=O)NCCCCNc1c(Cl)cc(c2c1nccc2)Cl
ONC(=O)CCCCCCOc1ccc(cc1)c1nnc(s1)c1ccccc1
O=C(c1ccc(cc1)CNC1=NCC(O1)c1ccccc1)Nc1ccccc1N
O=CN(CCCCCC(C(=O)Nc1ccc2c(c1)cccn2)C(=O)Nc1ccc2c(c1)cccn2)O
ONC(=O)C=Cc1ccc(cc1)NS(=O)(=O)c1cccc(c1)C
CCNNC(=O)c1ccc(cc1)CNC(=O)c1ccccc1
CNNC(=O)c1ccc(cc1)CNC(=O)c1ccccc1
SCC(=O)NCCCCNc1c(Cl)cc(c2c1nccc2)Cl
ONC(=O)CCCCC(=O)N1CCN(CC1)c1ccc(cn1)c1cc(C(=O)NCc2c(C)cc([nH]c2=O)C)c2c(c1)n(nc2)C(C)C
CNC(=O)C(=NO)CCCCCCC(=O)Nc1ccc(cc1)c1ccccc1
CCC(=C(c1ccccc1)c1ccc(cc1)OCCN(Cc1ccc(cc1)c1nnn(c1)CCCCCC(=O)NO)C)c1ccccc1
ONC(=O)c1ccc(cc1)Cc1ccc2c(c1)c(=O)n(c(n2)CC)CCc1ccccc1
ONC(=O)C=Cc1ccc2c(c1)nc(n(c2=O)CCc1ccccc1)C(C)C
ONC(=O)COc1ccc(c(c1)F)CNC1CCC(=CC1)c1c(C)[nH]c2c1cccc2
CSCCC1NC(=O)CC2C=CCCSSCC(NC1=O)C(=O)NC(C(C)C)C(CC(=O)O2)O
ONC(=O)c1cnc(nc1)N(CCOc1cc(cc2c1nc(N)nc2C)c1cnc(c(c1)C)OC)C
CCNNC(=O)c1ccc(cc1)Cn1c2ccccc2c2c1CCCC2
ONC(=O)c1cnc(nc1)N1CCN(CC1)c1ccc(cn1)c1cc(C(=O)NCc2c(C)cc([nH]c2=O)C)c2c(c1)n(cc2C)C(CC)C
ONC(=O)c1ccc(cc1)CN1C(=O)c2cccc3c2c(C1=O)ccc3OC
ONC(=O)c1

CCC(=O)CCCCCC(c1ncc(o1)c1cc2ccc(nc2cc1OC)C)NC(=O)C1CC21CCN(CC2)CC1CC1
ONC(=O)CCCCCCC(=O)Nc1n[nH]c2c1ccc(c2)c1ccc(cc1)OC
ONC(=O)CCCCCCn1ncc2c1nc(nc2N1CCOCC1)c1ccc(cc1)NC(=O)N1CCOC(C1)C
ONC(=O)C=Cc1ccc2c(c1)C(=O)c1c(C2=O)cccc1
O=C(Nc1scc(n1)c1cccc(c1)NC(=O)OC(C)(C)C)CCCCCC(=O)Nc1ccccc1N
CCOC(=O)Nc1cccc(c1)c1csc(n1)NC(=O)CCCCCC(=O)NO
SCCCCCC(C(=O)NC1CCCC1)NC(=O)OC(C)(C)C
ONC(=O)c1cnc(nc1)NC1(CC1)c1ccccc1
ONC(=O)c1cnc(nc1)N(C(C)C)CCOc1cc(cc2c1ncnc2C)c1cnc(c(c1)F)OC
ONC(=O)CCCCCCOc1cc(cc2c1ncnc2C)c1cnc(c(c1)NS(=O)(=O)c1ccc(cc1F)F)OC
ONC(=O)CCCCCCCOc1cc(cc2c1ncnc2C)c1cnc(c(c1)F)OC
ONC(=O)CCCCCCCCOc1cc(cc2c1ncnc2C)c1ccc(nc1)OC
ONC(=O)CCCOc1cc(cc2c1ncnc2C)c1ccc(nc1)OC
ONC(=O)CCCCCC(=O)N(c1ccc(cc1)OC)Cc1noc(n1)c1cccc(c1)F
COc1ccc(cc1OC)NS(=O)(=O)c1ccc(cc1)C=CC(=O)Nc1ccccc1N
ONC(=O)c1ccc(cc1)CCNC(=O)OC1CN(C(C1)c1nc2cccc(c2c(=O)n1C)Cl)c1nc(N)nc(c1C#N)N
O=C(c1ccc(cc1)CN1C(COC1=O)Cc1ccccc1)Nc1cc(ccc1N)c1cccs1
O=C(OCc1cccnc1)NCc1ccc(cc1)C(=O)Nc1ccccc1N
ONC(=O)c1ccc(cc1)Cn1c(=O)n(CCc2ccccc2)c(=O)c2c1

O=C(C=Cc1cnc2n1nccc2)NCc1ccc(cc1)C(=O)Nc1ccccc1N
O=C(c1ncc2c(c1)ccc(c2C1CC1)N1CCNCC1)Nc1ccccc1N
O=C(Nc1ccccc1N)C=Cc1ccc(nc1)NS(=O)(=O)c1ccc(cc1)c1ccccc1
ONC(=O)CCCCCCC(=O)Nc1ccccc1
ONC(=O)c1cnc(nc1)N1CCC(CC1)CNCc1cn(c2c1cccc2)C
CCCNNC(=O)c1ccc(cc1)CNC(=O)C=Cc1ccccc1
CCCNNC(=O)c1ccc(cc1)CNC(=O)c1cc2c([nH]1)ccc(c2)Br
ONC(=O)c1ccc(cc1)CNC(=O)N1CCC(CC1)N1CC(C1=O)(c1ccccc1)c1ccccc1
ONC(=O)CCCCCCC(=O)Nc1ccccc1
SCCCCCC(C(=O)Nc1ccccc1)NC(=O)C1CCCC(=O)N1
ONC(=O)c1coc(n1)c1ccc2c(c1)ccc(c2)OC
ONC(=O)CCCOc1cc(ccc1OC)Nc1nc(C)nc2c1cccc2
CC(=O)Nc1ccc(cc1)C(=O)Nc1ccc(cc1N)F
CSCCC1NC(=O)CC2C=CCCSSCC(NC1=O)C(=O)NC(C(CC)C)C(CC(=O)O2)O
ONC(=O)CCCCCC=Cc1csc(n1)Br
ONC(=O)CCCCNC(=O)c1nc(sc1C=C(C)C)c1nccs1
ONC(=O)CCCOc1cc(cc2c1ncnc2C)c1cnc(c(c1)NS(=O)(=O)c1ccc(cc1F)F)OC
ONC(=O)CCCCCCCOc1cc(cc2c1ncnc2C)c1ccc(nc1)OC
COc1ccc(cc1)C(=O)Nc1cc(ccc1N)c1cccs1
ONC(=O)c1ccc(cc1)c1ccncc1
ONC(=O)CCCCCOc1ccccc1N1C(=O)CSC1c1cccc(c1)Br
ONC(=O)c1cnc(nc1)NC1(CCCC1)c1ccccc1
N#Cc1ccc(cc1C(F)(F)F)N1C(=S)N(C(C1=O)(C)C)c1ccc(c(c1)F

O=C(Nc1ccccc1N)C=Cc1ccc(cc1)NS(=O)(=O)c1ccc(cc1)C
ONC(=O)CCCCCCCCn1ncc(c1)c1cnc2c(n1)cc(cc2)N(c1cc(OC)cc(c1)OC)CCNC(C)C
ONC(=O)c1ccc(cc1)OCCn1ncc(c1)c1cnc2c(n1)cc(cc2)N(c1cc(OC)cc(c1)OC)CCNC(C)C
ONC(=O)c1ccc(c(c1)F)Cn1c(C)nc2c1ccc(c2)NC(=O)CCOCCOCCOCCOCCNC(=O)COc1cccc2c1C(=O)N(C2=O)C1CCC(=O)NC1=O
COCCOc1ccccc1C(=O)NCCCCCC(=O)Nc1ccccc1N
ONC(=O)C=CC(=CC(C(=O)c1ccc(cc1)N(C)C)C)C
ONC(=O)CCCCCCC(=O)Nc1ccccc1
O=C(Nc1ccccc1N)CCCCCNC(=O)c1n[nH]c2c1cc(C)cc2
COc1ccc(cc1)C=C1SC(=O)N(C1=O)CCNC(=O)Nc1c(=O)n(n(c1C)C)c1ccccc1
ONC(=O)C=Cc1ccc(cc1)CN1CCc2c(C1)oc1c2ccc(c1)OC
COCCNc1cc2ncc(cc2cc1C1CC1)C(=O)Nc1cc(ccc1N)c1cccs1
O=C(c1ccc(cc1)CN(C(=O)O)Cc1cccnc1)Nc1cc(ccc1N)c1ccccc1
O=C(OCc1cccnc1)NCc1ccc(cc1)C(=O)Nc1ccccc1N
Cc1csc(c1)c1ccc(c(c1)NC(=O)c1ccc(cc1)CNc1ccncc1)N
O=C(c1ccc(cc1)CNCCCc1ccccc1)Nc1cc(ccc1O)c1ccccc1
CCN(Cc1ccc(cc1)C(=O)Nc1cc(ccc1O)c1ccccc1)C
ONC(=O)c1ccc(cc1Cl)Cn1ccc2c1ccc(c2)C(=O)NCC12CC3CC(C2)CC(C1)C3
ONC(=O)CCCCCCC(=O)Nc1ccccc1
O=C(Nc1ccccc1N)CCCCCNC(=O)c1ccc(cc1)C(C)(C)C
O=C(Nc1cc

O=C(c1ccc(cc1)Br)NNCCC1CCCC1
ONC(=O)CCCCCCC(=O)Nc1ccccc1
O=C(c1cnc2c(c1)ccc(c2)N1CCNCC1)Nc1cc(sc1N)c1ccccc1
ONC(=O)CCCCCCC(=O)Nc1ccccc1
CCC(=O)CCCCCC(c1ncc([nH]1)c1cnc2c(c1)cccc2)NC(=O)C1CC21CCN(CC2)C
ONC(=O)C=Cc1ccn(c1)S(=O)(=O)c1ccc(cc1)CN(C)C
ONC(=O)CCCCNC(=O)c1ncc(o1)c1ccccc1
ONC(=O)CCCCCCCNC(=O)c1ncc(o1)c1ccccc1
ONC(=O)CCCCCCNC(=O)c1ncc(o1)c1ccccc1C
ONC(=O)C=Cc1ccc(cc1)C=CC(=O)c1cccc(c1)NC(=O)OC(C)(C)C
ONC(=O)CCCCCNC(=O)c1ncc(s1)c1ccc(cc1)OC
ONC(=O)c1ccc(cc1)Cn1c2ccccc2c2c1CCN(C2)C
CCCNNC(=O)c1ccc(cc1)NCc1ccccc1
ONC(=O)CCCCCCC(=O)Nc1ccccc1
ONC(=O)CCCCCCC(=O)Nc1ccccc1
ONC(=O)CCCCCCCOc1ccc2c(c1)c1CCN3C(c1[nH]2)N(C)c1c(C3=O)cc(cc1)F
O=C(N1CCC(CC1)Nc1nc(SCc2ccc(cc2)C(=O)Nc2ccccc2N)nn2c1ccc2)OC(C)(C)C
ONC(=O)CCCCCCC(=O)Nc1ccccc1
CCCNNC(=O)c1ccc(cc1)NC(=O)c1ccccc1
ONC(=O)CCCCCCC(=O)Nc1ccccc1
ONC(=O)C=Cc1ccc(cc1)CNCCc1c(C)[nH]c2c1cccc2
ONC(=O)c1cnc(nc1)N1CCC(CC1)CNCc1cn(c2c1cccc2)C
ONC(=O)c1sc2c(c1Cl)cccc2
ONC(=O)CCCCCCn1cnc2c1nc(nc2N1CCOCC1)c1cccc(c1)CO
O=C(OCc1cccnc1)NCc1ccc(cc1)C(=O)N

In [30]:
df_chembl.shape[0], len(canonical_smiles)

(8345, 8345)

In [31]:
#inserimento colonna contenente canonical smiles
df_chembl['CANONICAL SMILES'] = canonical_smiles

In [32]:
df_chembl.head()

ID                                    ISOMERIC SMILES  \
0   CHEMBL148769        COc1ccc(NC(=O)Nc2ccc(/C=C/C(=O)NO)cc2)cc1OC   
1   CHEMBL346414  Cc1ccc(NS(=O)(=O)c2ccc(/C=C/C(=O)Nc3ccccc3N)cc...   
2  CHEMBL3916454          Nc1ccccc1NC(=O)CCCCCNS(=O)(=O)c1ccc(F)cc1   
3  CHEMBL3936525                Nc1ccccc1NC(=O)CCCCCNC(=O)c1ccccc1F   
4   CHEMBL327924        Nc1ccccc1NC(=O)CCCCCn1c(=O)[nH]c2ccccc2c1=O   

  STANDARD TYPE STANDARD RELATION  STANDARD VALUE STANDARD UNITS  ASSAY TYPE  \
0          IC50               '='          1000.0             nM           B   
1          IC50               '='          2000.0             nM           B   
2          IC50               '='         24000.0             nM           B   
3          IC50               '='          1135.0             nM           B   
4          IC50               '='          4000.0             nM           B   

           MW  STANDARD VALUE [nM]      pAct  \
0  357.132471               1000.0  6.000000   
1  407.130363               2000.0  5.698970   
2  379.136591              24000.0  4.619789   
3  343.169605               1135.0  5.945004   
4  366.169191               4000.0  5.397940   

                                    CANONICAL SMILES  
0        ONC(=O)C=Cc1ccc(cc1)NC(=O)Nc1ccc(c(c1)OC)OC  
1  O=C(Nc1ccccc1N)C=Cc1ccc(cc1)S(=O)(=O)Nc1ccc(cc1)C  
2          O=C(Nc1ccccc1N)CCCCCNS(=O)(=O)c1ccc(cc1)F  
3                O=C(Nc1ccccc1N)CCCCCNC(=O)c1ccccc1F  
4      O=C(Nc1ccccc1N)CCCCCn1c(=O)[nH]c2c(c1=O)cccc2

In [39]:
# versione con pybel
#generazione inchi privi di eventuali proprietà stereoisomeriche
inchi = [] 
for smi in df_chembl['CANONICAL SMILES']:
    inchi.append(pybel.readstring('smi', smi).write('inchi'))

In [40]:
inchi_no_space = [i.strip() for i in inchi]

In [41]:
len(inchi_no_space)

8345

In [42]:
inchi_no_space[-1], inchi[-1]

('InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)10-6-1-2-7-11-14(18)16-19/h3-5,8-9,19H,1-2,6-7,10-11H2,(H,15,17)(H,16,18)',
 'InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)10-6-1-2-7-11-14(18)16-19/h3-5,8-9,19H,1-2,6-7,10-11H2,(H,15,17)(H,16,18)\n')

In [43]:
#inserimento colonna contenente inchi senza \n alla fine perchè ho usato strip
df_chembl['INCHI'] = inchi_no_space

In [44]:
df_chembl.head()

ID                                    ISOMERIC SMILES  \
0   CHEMBL148769        COc1ccc(NC(=O)Nc2ccc(/C=C/C(=O)NO)cc2)cc1OC   
1   CHEMBL346414  Cc1ccc(NS(=O)(=O)c2ccc(/C=C/C(=O)Nc3ccccc3N)cc...   
2  CHEMBL3916454          Nc1ccccc1NC(=O)CCCCCNS(=O)(=O)c1ccc(F)cc1   
3  CHEMBL3936525                Nc1ccccc1NC(=O)CCCCCNC(=O)c1ccccc1F   
4   CHEMBL327924        Nc1ccccc1NC(=O)CCCCCn1c(=O)[nH]c2ccccc2c1=O   

  STANDARD TYPE STANDARD RELATION  STANDARD VALUE STANDARD UNITS  ASSAY TYPE  \
0          IC50               '='          1000.0             nM           B   
1          IC50               '='          2000.0             nM           B   
2          IC50               '='         24000.0             nM           B   
3          IC50               '='          1135.0             nM           B   
4          IC50               '='          4000.0             nM           B   

           MW  STANDARD VALUE [nM]      pAct  \
0  357.132471               1000.0  6.000000   
1  407.130363               2000.0  5.698970   
2  379.136591              24000.0  4.619789   
3  343.169605               1135.0  5.945004   
4  366.169191               4000.0  5.397940   

                                    CANONICAL SMILES  \
0        ONC(=O)C=Cc1ccc(cc1)NC(=O)Nc1ccc(c(c1)OC)OC   
1  O=C(Nc1ccccc1N)C=Cc1ccc(cc1)S(=O)(=O)Nc1ccc(cc1)C   
2          O=C(Nc1ccccc1N)CCCCCNS(=O)(=O)c1ccc(cc1)F   
3                O=C(Nc1ccccc1N)CCCCCNC(=O)c1ccccc1F   
4      O=C(Nc1ccccc1N)CCCCCn1c(=O)[nH]c2c(c1=O)cccc2   

                                               INCHI  
0  InChI=1S/C18H19N3O5/c1-25-15-9-8-14(11-16(15)2...  
1  InChI=1S/C22H21N3O3S/c1-16-6-11-18(12-7-16)25-...  
2  InChI=1S/C18H22FN3O3S/c19-14-9-11-15(12-10-14)...  
3  InChI=1S/C19H22FN3O2/c20-15-9-4-3-8-14(15)19(2...  
4  InChI=1S/C20H22N4O3/c21-15-9-4-6-11-17(15)22-1...

In [45]:
df_chembl = df_chembl.reset_index()
df_chembl.index

RangeIndex(start=0, stop=8345, step=1)

In [46]:
#inizializzazione dell'indice e selezione colonne
df_chembl = df_chembl[['ID', 'INCHI','ISOMERIC SMILES', 'CANONICAL SMILES', 'STANDARD RELATION', 'STANDARD VALUE [nM]', 'pAct']]

In [47]:
df_chembl.head()

ID                                              INCHI  \
0   CHEMBL148769  InChI=1S/C18H19N3O5/c1-25-15-9-8-14(11-16(15)2...   
1   CHEMBL346414  InChI=1S/C22H21N3O3S/c1-16-6-11-18(12-7-16)25-...   
2  CHEMBL3916454  InChI=1S/C18H22FN3O3S/c19-14-9-11-15(12-10-14)...   
3  CHEMBL3936525  InChI=1S/C19H22FN3O2/c20-15-9-4-3-8-14(15)19(2...   
4   CHEMBL327924  InChI=1S/C20H22N4O3/c21-15-9-4-6-11-17(15)22-1...   

                                     ISOMERIC SMILES  \
0        COc1ccc(NC(=O)Nc2ccc(/C=C/C(=O)NO)cc2)cc1OC   
1  Cc1ccc(NS(=O)(=O)c2ccc(/C=C/C(=O)Nc3ccccc3N)cc...   
2          Nc1ccccc1NC(=O)CCCCCNS(=O)(=O)c1ccc(F)cc1   
3                Nc1ccccc1NC(=O)CCCCCNC(=O)c1ccccc1F   
4        Nc1ccccc1NC(=O)CCCCCn1c(=O)[nH]c2ccccc2c1=O   

                                    CANONICAL SMILES STANDARD RELATION  \
0        ONC(=O)C=Cc1ccc(cc1)NC(=O)Nc1ccc(c(c1)OC)OC               '='   
1  O=C(Nc1ccccc1N)C=Cc1ccc(cc1)S(=O)(=O)Nc1ccc(cc1)C               '='   
2          O=C(Nc1ccccc1N)CCCCCNS(=O)(=O)c1ccc(cc1)F               '='   
3                O=C(Nc1ccccc1N)CCCCCNC(=O)c1ccccc1F               '='   
4      O=C(Nc1ccccc1N)CCCCCn1c(=O)[nH]c2c(c1=O)cccc2               '='   

   STANDARD VALUE [nM]      pAct  
0               1000.0  6.000000  
1               2000.0  5.698970  
2              24000.0  4.619789  
3               1135.0  5.945004  
4               4000.0  5.397940

In [48]:
df_chembl.index

RangeIndex(start=0, stop=8345, step=1)

In [49]:
df_chembl['INCHI'].duplicated()

0       False
1       False
2       False
3       False
4       False
5       False
6       False
7       False
8       False
9       False
10      False
11      False
12      False
13      False
14      False
15      False
16      False
17      False
18      False
19      False
20      False
21      False
22      False
23      False
24      False
25      False
26      False
27      False
28      False
29      False
30      False
31      False
32      False
33      False
34      False
35      False
36      False
37      False
38      False
39      False
40      False
41      False
42      False
43      False
44      False
45      False
46      False
47      False
48      False
49      False
50      False
51      False
52      False
53      False
54      False
55      False
56      False
57      False
58      False
59      False
60      False
61      False
62      False
63      False
64      False
65      False
66      False
67      False
68      False
69      False
70      False
71    

Parameters (.duplicated):
subset (optional, for DataFrame): non serve se lo faccio già su una colonna

Specifies columns to consider when identifying duplicates. Default is None, meaning all columns are used.
Example: subset=['col1', 'col2']
keep (optional):

Determines which duplicate(s) to mark as non-duplicate:
'first': Marks duplicates except for the first occurrence (default).
'last': Marks duplicates except for the last occurrence.
False: Marks all duplicates as True.

In [50]:
df_chembl[df_chembl['INCHI'].duplicated()]

ID                                              INCHI  \
71         CHEMBL98  InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...   
73         CHEMBL98  InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...   
76      CHEMBL98911  InChI=1S/C13H18N2O3/c16-12(11-6-5-9-14-10-11)7...   
148        CHEMBL99  InChI=1S/C17H22N2O3/c1-12(5-10-16(20)18-22)11-...   
164     CHEMBL95885  InChI=1S/C15H21NO4/c1-20-14-10-7-6-8-12(14)13(...   
173        CHEMBL99  InChI=1S/C17H22N2O3/c1-12(5-10-16(20)18-22)11-...   
174        CHEMBL98  InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...   
224     CHEMBL27759  InChI=1S/C21H20N4O3/c22-18-5-1-2-6-19(18)25-20...   
226    CHEMBL475796  InChI=1S/C30H27N7O/c1-20-8-13-24(17-28(20)37-3...   
231        CHEMBL98  InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...   
233   CHEMBL5272849  InChI=1S/C19H25N3O3S/c1-13-16(17(22-25-13)15-9...   
250   CHEMBL4645468  InChI=1S/C30H39N5O3/c1-4-21(36)11-6-5-7-13-25(...   
276   CHEMBL2018302  InChI=1S/C20H21N3O2/c1-22-11-10-19-17(13-22)16...   
278    CHEMBL483254  InChI=1S/C21H23N3O2/c1-15-18(19-4-2-3-5-20(19)...   
309        CHEMBL99  InChI=1S/C17H22N2O3/c1-12(5-10-16(20)18-22)11-...   
310    CHEMBL164868  InChI=1S/C17H22N2O3/c1-12(5-10-16(20)18-22)11-...   
315   CHEMBL2018302  InChI=1S/C20H21N3O2/c1-22-11-10-19-17(13-22)16...   
319        CHEMBL98  InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...   
321    CHEMBL583130  InChI=1S/C31H45N5O5/c1-5-23(37)11-7-6-8-14-26-...   
322    CHEMBL585939  InChI=1S/C29H42N6O6/c1-17(2)13-20-15-26(37)31-...   
337        CHEMBL98  InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...   
339        CHEMBL98  InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...   
355    CHEMBL393464  InChI=1S/C30H39N5O4S2/c1-21-28(38)35-18-11-15-...   
356   CHEMBL3828496  InChI=1S/C18H19FN2O2/c19-14-7-4-12(5-8-14)13-6...   
362        CHEMBL98  InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...   
365        CHEMBL98  InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...   
367   CHEMBL2018302  InChI=1S/C20H21N3O2/c1-22-11-10-19-17(13-22)16...   
393        CHEMBL98  InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...   
403   CHEMBL2057829  InChI=1S/C16H15N9O2/c17-13-6-5-12(23-25-19)9-1...   
415   CHEMBL2364628  InChI=1S/C24H27N5O3/c30-22(28-32)15-9-1-2-10-1...   
417        CHEMBL98  InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...   
418   CHEMBL2018302  InChI=1S/C20H21N3O2/c1-22-11-10-19-17(13-22)16...   
441        CHEMBL98  InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...   
448    CHEMBL515295  InChI=1S/C16H22N4O4S/c1-24-13-10-12-6-5-8-18-1...   
457   CHEMBL2018302  InChI=1S/C20H21N3O2/c1-22-11-10-19-17(13-22)16...   
464   CHEMBL3287009  InChI=1S/C26H37N3O4S3/c1-5-6-7-8-10-13-22(30)3...   
473     CHEMBL27759  InChI=1S/C21H20N4O3/c22-18-5-1-2-6-19(18)25-20...   
475        CHEMBL99  InChI=1S/C17H22N2O3/c1-12(5-10-16(20)18-22)11-...   
477        CHEMBL98  InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...   
478        CHEMBL98  InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...   
494     CHEMBL95885  InChI=1S/C15H21NO4/c1-20-14-10-7-6-8-12(14)13(...   
539        CHEMBL98  InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...   
545    CHEMBL169352  InChI=1S/C25H21N3O3S/c26-22-9-3-4-10-23(22)27-...   
547        CHEMBL98  InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...   
561        CHEMBL98  InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...   
565    CHEMBL462208  InChI=1S/C15H12F3NO2S/c1-9(10-5-3-2-4-6-10)19-...   
590        CHEMBL98  InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...   
592     CHEMBL27759  InChI=1S/C21H20N4O3/c22-18-5-1-2-6-19(18)25-20...   
602   CHEMBL2448576  InChI=1S/C27H35N5O3/c1-4-20(33)11-6-5-7-13-23(...   
603   CHEMBL4086442  InChI=1S/C30H33N5O4/c1-3-16-33-35-29(37)22-10-...   
635        CHEMBL98  InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...   
640   CHEMBL4856550  InChI=1S/C23H27N3O5/c1-13-4-9-20(31-13)19-11-1...   
715   CHEMBL3126833  InChI=1S/C22H35N3O6S3/c1-13(2)20-17(26)11-19(2...   
720        CHEMBL98  

In [51]:
inchi_duplicated = df_chembl['INCHI'][df_chembl['INCHI'].duplicated()]
len(inchi_duplicated)

1614

In [52]:
inchi_duplicated

71      InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...
73      InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...
76      InChI=1S/C13H18N2O3/c16-12(11-6-5-9-14-10-11)7...
148     InChI=1S/C17H22N2O3/c1-12(5-10-16(20)18-22)11-...
164     InChI=1S/C15H21NO4/c1-20-14-10-7-6-8-12(14)13(...
173     InChI=1S/C17H22N2O3/c1-12(5-10-16(20)18-22)11-...
174     InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...
224     InChI=1S/C21H20N4O3/c22-18-5-1-2-6-19(18)25-20...
226     InChI=1S/C30H27N7O/c1-20-8-13-24(17-28(20)37-3...
231     InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...
233     InChI=1S/C19H25N3O3S/c1-13-16(17(22-25-13)15-9...
250     InChI=1S/C30H39N5O3/c1-4-21(36)11-6-5-7-13-25(...
276     InChI=1S/C20H21N3O2/c1-22-11-10-19-17(13-22)16...
278     InChI=1S/C21H23N3O2/c1-15-18(19-4-2-3-5-20(19)...
309     InChI=1S/C17H22N2O3/c1-12(5-10-16(20)18-22)11-...
310     InChI=1S/C17H22N2O3/c1-12(5-10-16(20)18-22)11-...
315     InChI=1S/C20H21N3O2/c1-22-11-10-19-17(13-22)16...
319     InChI=

In [53]:
len(df_chembl[df_chembl['INCHI'].isin(inchi_duplicated)])#row dataframe che hanno inchi duplicato sono più di inchi_duplicated perchè ci sono tutte le copie

2251

In [54]:
#selezione e visualizzazione dei duplicati
duplicates = df_chembl[df_chembl['INCHI'].isin(inchi_duplicated)].sort_values('INCHI') 
len(duplicates)

2251

In [55]:
duplicates.head()

ID                                              INCHI  \
6046   CHEMBL512516  InChI=1S/C10H7F3N2O4S2/c1-21(17,18)4-7-14-9(19...   
4159   CHEMBL512516  InChI=1S/C10H7F3N2O4S2/c1-21(17,18)4-7-14-9(19...   
5887  CHEMBL4283263  InChI=1S/C11H10N4O/c12-8-3-1-2-4-9(8)15-11(16)...   
6427  CHEMBL4283263  InChI=1S/C11H10N4O/c12-8-3-1-2-4-9(8)15-11(16)...   
7670  CHEMBL4283263  InChI=1S/C11H10N4O/c12-8-3-1-2-4-9(8)15-11(16)...   

                                  ISOMERIC SMILES  \
6046  CS(=O)(=O)Cc1noc(-c2ccc(C(=O)C(F)(F)F)s2)n1   
4159  CS(=O)(=O)Cc1noc(-c2ccc(C(=O)C(F)(F)F)s2)n1   
5887                      Nc1ccccc1NC(=O)c1cnccn1   
6427                      Nc1ccccc1NC(=O)c1cnccn1   
7670                      Nc1ccccc1NC(=O)c1cnccn1   

                                CANONICAL SMILES STANDARD RELATION  \
6046  O=C(C(F)(F)F)c1ccc(s1)c1onc(n1)CS(=O)(=O)C               '='   
4159  O=C(C(F)(F)F)c1ccc(s1)c1onc(n1)CS(=O)(=O)C               '='   
5887                     O=C(c1cnccn1)Nc1ccccc1N               '='   
6427                     O=C(c1cnccn1)Nc1ccccc1N               '='   
7670                     O=C(c1cnccn1)Nc1ccccc1N               '='   

      STANDARD VALUE [nM]      pAct  
6046               2470.0  5.607303  
4159               2700.0  5.568636  
5887               2302.0  5.637895  
6427               2302.0  5.637895  
7670               2000.0  5.698970

In [56]:
duplicates.shape

(2251, 7)

In [57]:
df_chembl.shape

(8345, 7)

In [58]:
df = df_chembl[~df_chembl['INCHI'].duplicated(keep=False)]

In [59]:
df.shape

(6094, 7)

In [60]:
#inserimento colonne strutture molecolari
PandasTools.AddMoleculeColumnToFrame(frame=duplicates, smilesCol='ISOMERIC SMILES', molCol='ISOMERIC MOLECULES') 
PandasTools.AddMoleculeColumnToFrame(frame=duplicates, smilesCol='CANONICAL SMILES', molCol='CANONICAL MOLECULES')

In [61]:
duplicates.shape

(2251, 9)

In [64]:
duplicates.head()

ID                                              INCHI  \
6046   CHEMBL512516  InChI=1S/C10H7F3N2O4S2/c1-21(17,18)4-7-14-9(19...   
4159   CHEMBL512516  InChI=1S/C10H7F3N2O4S2/c1-21(17,18)4-7-14-9(19...   
5887  CHEMBL4283263  InChI=1S/C11H10N4O/c12-8-3-1-2-4-9(8)15-11(16)...   
6427  CHEMBL4283263  InChI=1S/C11H10N4O/c12-8-3-1-2-4-9(8)15-11(16)...   
7670  CHEMBL4283263  InChI=1S/C11H10N4O/c12-8-3-1-2-4-9(8)15-11(16)...   

                                  ISOMERIC SMILES  \
6046  CS(=O)(=O)Cc1noc(-c2ccc(C(=O)C(F)(F)F)s2)n1   
4159  CS(=O)(=O)Cc1noc(-c2ccc(C(=O)C(F)(F)F)s2)n1   
5887                      Nc1ccccc1NC(=O)c1cnccn1   
6427                      Nc1ccccc1NC(=O)c1cnccn1   
7670                      Nc1ccccc1NC(=O)c1cnccn1   

                                CANONICAL SMILES STANDARD RELATION  \
6046  O=C(C(F)(F)F)c1ccc(s1)c1onc(n1)CS(=O)(=O)C               '='   
4159  O=C(C(F)(F)F)c1ccc(s1)c1onc(n1)CS(=O)(=O)C               '='   
5887                     O=C(c1cnccn1)Nc1ccccc1N               '='   
6427                     O=C(c1cnccn1)Nc1ccccc1N               '='   
7670                     O=C(c1cnccn1)Nc1ccccc1N               '='   

      STANDARD VALUE [nM]      pAct  \
6046               2470.0  5.607303   
4159               2700.0  5.568636   
5887               2302.0  5.637895   
6427               2302.0  5.637895   
7670               2000.0  5.698970   

                                    ISOMERIC MOLECULES  \
6046  <rdkit.Chem.rdchem.Mol object at 0x7f00cd0d0510>   
4159  <rdkit.Chem.rdchem.Mol object at 0x7f00cd0d0820>   
5887  <rdkit.Chem.rdchem.Mol object at 0x7f00cd0d09e0>   
6427  <rdkit.Chem.rdchem.Mol object at 0x7f00cd0d0350>   
7670  <rdkit.Chem.rdchem.Mol object at 0x7f00cd0d0740>   

                                   CANONICAL MOLECULES  
6046  <rdkit.Chem.rdchem.Mol object at 0x7f00cd0d07b0>  
4159  <rdkit.Chem.rdchem.Mol object at 0x7f00ccbfb220>  
5887  <rdkit.Chem.rdchem.Mol object at 0x7f00ccbfb290>  
6427  <rdkit.Chem.rdchem.Mol object at 0x7f00ccbfb300>  
7670  <rdkit.Chem.rdchem.Mol object at 0x7f00ccbfb370>

In [65]:
duplicates.index

Int64Index([6046, 4159, 5887, 6427, 7670, 4264, 3792, 5489, 7414, 5586,
            ...
            5629, 6290, 7914, 8318,  371,  895, 4024,  195, 3626, 2638],
           dtype='int64', length=2251)

In [66]:
duplicates['ISOMERIC SMILES']

6046          CS(=O)(=O)Cc1noc(-c2ccc(C(=O)C(F)(F)F)s2)n1
4159          CS(=O)(=O)Cc1noc(-c2ccc(C(=O)C(F)(F)F)s2)n1
5887                              Nc1ccccc1NC(=O)c1cnccn1
6427                              Nc1ccccc1NC(=O)c1cnccn1
7670                              Nc1ccccc1NC(=O)c1cnccn1
4264                    O=C(NCCS)/C(Cc1ccc(O)c(Br)c1)=N/O
3792                    O=C(NCCS)/C(Cc1ccc(O)c(Br)c1)=N/O
5489                              CCCCNNC(=O)c1ccc(Br)cc1
7414                              CCCCNNC(=O)c1ccc(Br)cc1
5586                              CCCCNNC(=O)c1ccc(Br)cc1
5032                         O=C(CCCCC/C=C\c1csc(Br)n1)NO
6061                         O=C(CCCCC/C=C/c1csc(Br)n1)NO
604                 O=C(NCCO)c1ccc(-c2noc(C(F)(F)F)n2)cc1
5269                O=C(NCCO)c1ccc(-c2noc(C(F)(F)F)n2)cc1
6701        CCCS(=O)(=O)Cc1noc(-c2ccc(C(=O)C(F)(F)F)s2)n1
3486        CCCS(=O)(=O)Cc1noc(-c2ccc(C(=O)C(F)(F)F)s2)n1
2245                              Nc1ccccc1NC(=O)c1cccnc1
1664          

In [67]:
prova_influenza_index = duplicates.reset_index()

In [68]:
prova_influenza_index['ISOMERIC SMILES']

0             CS(=O)(=O)Cc1noc(-c2ccc(C(=O)C(F)(F)F)s2)n1
1             CS(=O)(=O)Cc1noc(-c2ccc(C(=O)C(F)(F)F)s2)n1
2                                 Nc1ccccc1NC(=O)c1cnccn1
3                                 Nc1ccccc1NC(=O)c1cnccn1
4                                 Nc1ccccc1NC(=O)c1cnccn1
5                       O=C(NCCS)/C(Cc1ccc(O)c(Br)c1)=N/O
6                       O=C(NCCS)/C(Cc1ccc(O)c(Br)c1)=N/O
7                                 CCCCNNC(=O)c1ccc(Br)cc1
8                                 CCCCNNC(=O)c1ccc(Br)cc1
9                                 CCCCNNC(=O)c1ccc(Br)cc1
10                           O=C(CCCCC/C=C\c1csc(Br)n1)NO
11                           O=C(CCCCC/C=C/c1csc(Br)n1)NO
12                  O=C(NCCO)c1ccc(-c2noc(C(F)(F)F)n2)cc1
13                  O=C(NCCO)c1ccc(-c2noc(C(F)(F)F)n2)cc1
14          CCCS(=O)(=O)Cc1noc(-c2ccc(C(=O)C(F)(F)F)s2)n1
15          CCCS(=O)(=O)Cc1noc(-c2ccc(C(=O)C(F)(F)F)s2)n1
16                                Nc1ccccc1NC(=O)c1cccnc1
17            

In [69]:
# analisi di centri chirali
configuration = [] 
for i in duplicates['ISOMERIC SMILES']:
    mol = Chem.MolFromSmiles(i) 
    configuration.append(Chem.FindMolChiralCenters(mol)) 

In [71]:
configuration

[[],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [(1, 'R')],
 [(1, 'S')],
 [],
 [],
 [],
 [],
 [],
 [],
 [(1, 'S')],
 [(1, 'R')],
 [],
 [(1, 'R')],
 [(1, 'S')],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [(3, 'R')],
 [(3, 'S')],
 [],
 [],
 [],
 [],
 [],
 [(3, 'S')],
 [(3, 'R')],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],


In [72]:
len(configuration)

2251

In [73]:
# inserisco i dati di centri chirali nel dataframe dei duplicati
duplicates['Configuration'] = configuration

In [74]:
duplicates.index

Int64Index([6046, 4159, 5887, 6427, 7670, 4264, 3792, 5489, 7414, 5586,
            ...
            5629, 6290, 7914, 8318,  371,  895, 4024,  195, 3626, 2638],
           dtype='int64', length=2251)

In [75]:
duplicates.columns

Index(['ID', 'INCHI', 'ISOMERIC SMILES', 'CANONICAL SMILES',
       'STANDARD RELATION', 'STANDARD VALUE [nM]', 'pAct',
       'ISOMERIC MOLECULES', 'CANONICAL MOLECULES', 'Configuration'],
      dtype='object')

In [76]:
#controllo
duplicates = duplicates.reset_index() 
duplicates = duplicates[['ID', 'INCHI','ISOMERIC SMILES', 'pAct', 'ISOMERIC MOLECULES', 'Configuration', 'STANDARD RELATION']] 
duplicates.head()

ID                                              INCHI  \
0   CHEMBL512516  InChI=1S/C10H7F3N2O4S2/c1-21(17,18)4-7-14-9(19...   
1   CHEMBL512516  InChI=1S/C10H7F3N2O4S2/c1-21(17,18)4-7-14-9(19...   
2  CHEMBL4283263  InChI=1S/C11H10N4O/c12-8-3-1-2-4-9(8)15-11(16)...   
3  CHEMBL4283263  InChI=1S/C11H10N4O/c12-8-3-1-2-4-9(8)15-11(16)...   
4  CHEMBL4283263  InChI=1S/C11H10N4O/c12-8-3-1-2-4-9(8)15-11(16)...   

                               ISOMERIC SMILES      pAct  \
0  CS(=O)(=O)Cc1noc(-c2ccc(C(=O)C(F)(F)F)s2)n1  5.607303   
1  CS(=O)(=O)Cc1noc(-c2ccc(C(=O)C(F)(F)F)s2)n1  5.568636   
2                      Nc1ccccc1NC(=O)c1cnccn1  5.637895   
3                      Nc1ccccc1NC(=O)c1cnccn1  5.637895   
4                      Nc1ccccc1NC(=O)c1cnccn1  5.698970   

                                 ISOMERIC MOLECULES Configuration  \
0  <rdkit.Chem.rdchem.Mol object at 0x7f00cd0d0510>            []   
1  <rdkit.Chem.rdchem.Mol object at 0x7f00cd0d0820>            []   
2  <rdkit.Chem.rdchem.Mol object at 0x7f00cd0d09e0>            []   
3  <rdkit.Chem.rdchem.Mol object at 0x7f00cd0d0350>            []   
4  <rdkit.Chem.rdchem.Mol object at 0x7f00cd0d0740>            []   

  STANDARD RELATION  
0               '='  
1               '='  
2               '='  
3               '='  
4               '='

In [77]:
duplicates

ID                                              INCHI  \
0      CHEMBL512516  InChI=1S/C10H7F3N2O4S2/c1-21(17,18)4-7-14-9(19...   
1      CHEMBL512516  InChI=1S/C10H7F3N2O4S2/c1-21(17,18)4-7-14-9(19...   
2     CHEMBL4283263  InChI=1S/C11H10N4O/c12-8-3-1-2-4-9(8)15-11(16)...   
3     CHEMBL4283263  InChI=1S/C11H10N4O/c12-8-3-1-2-4-9(8)15-11(16)...   
4     CHEMBL4283263  InChI=1S/C11H10N4O/c12-8-3-1-2-4-9(8)15-11(16)...   
5     CHEMBL2047540  InChI=1S/C11H13BrN2O3S/c12-8-5-7(1-2-10(8)15)6...   
6     CHEMBL2047540  InChI=1S/C11H13BrN2O3S/c12-8-5-7(1-2-10(8)15)6...   
7     CHEMBL4303643  InChI=1S/C11H15BrN2O/c1-2-3-8-13-14-11(15)9-4-...   
8     CHEMBL4303643  InChI=1S/C11H15BrN2O/c1-2-3-8-13-14-11(15)9-4-...   
9     CHEMBL4303643  InChI=1S/C11H15BrN2O/c1-2-3-8-13-14-11(15)9-4-...   
10    CHEMBL5193020  InChI=1S/C11H15BrN2O2S/c12-11-13-9(8-17-11)6-4...   
11    CHEMBL5174162  InChI=1S/C11H15BrN2O2S/c12-11-13-9(8-17-11)6-4...   
12    CHEMBL3688152  InChI=1S/C12H10F3N3O3/c13-12(14,15)11-17-9(18-...   
13    CHEMBL3688152  InChI=1S/C12H10F3N3O3/c13-12(14,15)11-17-9(18-...   
14     CHEMBL471173  InChI=1S/C12H11F3N2O4S2/c1-2-5-23(19,20)6-9-16...   
15     CHEMBL471173  InChI=1S/C12H11F3N2O4S2/c1-2-5-23(19,20)6-9-16...   
16     CHEMBL236678  InChI=1S/C12H11N3O/c13-10-5-1-2-6-11(10)15-12(...   
17     CHEMBL236678  InChI=1S/C12H11N3O/c13-10-5-1-2-6-11(10)15-12(...   
18     CHEMBL236678  InChI=1S/C12H11N3O/c13-10-5-1-2-6-11(10)15-12(...   
19    CHEMBL2047684  InChI=1S/C12H14BrN3O5/c13-8-5-7(1-2-10(8)17)6-...   
20    CHEMBL2047684  InChI=1S/C12H14BrN3O5/c13-8-5-7(1-2-10(8)17)6-...   
21    CHEMBL3287021  InChI=1S/C12H14N4O3S2/c17-10(16-19)3-1-2-4-13-...   
22    CHEMBL3287021  InChI=1S/C12H14N4O3S2/c17-10(16-19)3-1-2-4-13-...   
23    CHEMBL3287023  InChI=1S/C12H14N4O3S2/c17-9(16-19)3-1-2-4-13-1...   
24    CHEMBL3287023  InChI=1S/C12H14N4O3S2/c17-9(16-19)3-1-2-4-13-1...   
25     CHEMBL242039  InChI=1S/C12H14O2S3/c1-3-16-12(15)17-8-11(13)9...   
26     CHEMBL242039  InChI=1S/C12H14O2S3/c1-3-16-12(15)17-8-11(13)9...   
27      CHEMBL95152  InChI=1S/C12H15NO3/c14-11(10-6-2-1-3-7-10)8-4-...   
28      CHEMBL95152  InChI=1S/C12H15NO3/c14-11(10-6-2-1-3-7-10)8-4-...   
29      CHEMBL95152  InChI=1S/C12H15NO3/c14-11(10-6-2-1-3-7-10)8-4-...   
30      CHEMBL99394  InChI=1S/C12H17NO3S/c14-10(11-7-5-9-17-11)6-3-...   
31      CHEMBL99394  InChI=1S/C12H17NO3S/c14-10(11-7-5-9-17-11)6-3-...   
32    CHEMBL5191682  InChI=1S/C13H11Br4N7O2/c14-8-9(15)11(17)13-12(...   
33    CHEMBL5191682  InChI=1S/C13H11Br4N7O2/c14-8-9(15)11(17)13-12(...   
34    CHEMBL4469488  InChI=1S/C13H11Cl2N3O4/c14-9-2-1-7(5-10(9)15)1...   
35    CHEMBL4469488  InChI=1S/C13H11Cl2N3O4/c14-9-2-1-7(5-10(9)15)1...   
36    CHEMBL4469488  InChI=1S/C13H11Cl2N3O4/c14-9-2-1-7(5-10(9)15)1...   
37    CHEMBL4469488  InChI=1S/C13H11Cl2N3O4/c14-9-2-1-7(5-10(9)15)1...   
38    CHEMBL3688166  InChI=1S/C13H12F3N3O3/c1-7(6-20)17-11(21)9-4-2...   
39    CHEMBL3692586  InChI=1S/C13H12F3N3O3/c1-7(6-20)17-11(21)9-4-2...   
40     CHEMBL269538  InChI=1S/C13H12N2O/c1-8-13-11(5-6-14-8)10-4-3-...   
41     CHEMBL269538  InChI=1S/C13H12N2O/c1-8-13-11(5-6-14-8)10-4-3-...   
42     CHEMBL269538  InChI=1S/C13H12N2O/c1-8-13-11(5-6-14-8)10-4-3-...   
43      CHEMBL98345  InChI=1S/C13H12N2O4S/c16-13(14-17)10-6-8-11(9-...   
44      CHEMBL98345  InChI=1S/C13H12N2O4S/c16-13(14-17)10-6-8-11(9-...   
45    CHEMBL3655915  InChI=1S/C13H14N4O2/c1-9(10-5-3-2-4-6-10)16-13...   
46    CHEMBL3655943  InChI=1S/C13H14N4O2/c1-9(10-5-3-2-4-6-10)16-13...   
47    CHEMBL3655944  InChI=1S/C13H14N4O2/c1-9(10-5-3-2-4-6-10)16-13...   
48    CHEMBL3655915  InChI=1S/C13H14N4O2/c1-9(10-5-3-2-4-6-10)16-13...   
49    CHEMBL3655944  InChI=1S/C13H14N4O2/c1-9(10-5-3-2-4-6-10)16-13...   
50    CHEMBL3655943  InChI=1S/C13H14N4O2/c1-9(10-5-3-2-4-6-10)16-13...   
51    CHEMBL2047685  InChI=1S/C13H16BrN3O5/c14-9-6-8(3-4-11(9)18)7-...   
52    CHEMBL2047685  InChI=1S/C13H16BrN3O5/c14-9-6-8(3-4-11(9)18)7-...   
53    CHEMBL5181798  

In [78]:
duplicates.index #sono mix di chirali e achirali

RangeIndex(start=0, stop=2251, step=1)

In [79]:
duplicates.isna().any()

ID                    False
INCHI                 False
ISOMERIC SMILES       False
pAct                  False
ISOMERIC MOLECULES    False
Configuration         False
STANDARD RELATION     False
dtype: bool

In [80]:
dupl = duplicates.groupby('INCHI').agg(lambda x: list(x))

In [81]:
dupl

ID  \
INCHI                                                                                                   
InChI=1S/C10H7F3N2O4S2/c1-21(17,18)4-7-14-9(19-...                       [CHEMBL512516, CHEMBL512516]   
InChI=1S/C11H10N4O/c12-8-3-1-2-4-9(8)15-11(16)1...      [CHEMBL4283263, CHEMBL4283263, CHEMBL4283263]   
InChI=1S/C11H13BrN2O3S/c12-8-5-7(1-2-10(8)15)6-...                     [CHEMBL2047540, CHEMBL2047540]   
InChI=1S/C11H15BrN2O/c1-2-3-8-13-14-11(15)9-4-6...      [CHEMBL4303643, CHEMBL4303643, CHEMBL4303643]   
InChI=1S/C11H15BrN2O2S/c12-11-13-9(8-17-11)6-4-...                     [CHEMBL5193020, CHEMBL5174162]   
InChI=1S/C12H10F3N3O3/c13-12(14,15)11-17-9(18-2...                     [CHEMBL3688152, CHEMBL3688152]   
InChI=1S/C12H11F3N2O4S2/c1-2-5-23(19,20)6-9-16-...                       [CHEMBL471173, CHEMBL471173]   
InChI=1S/C12H11N3O/c13-10-5-1-2-6-11(10)15-12(1...         [CHEMBL236678, CHEMBL236678, CHEMBL236678]   
InChI=1S/C12H14BrN3O5/c13-8-5-7(1-2-10(8)17)6-9...                     [CHEMBL2047684, CHEMBL2047684]   
InChI=1S/C12H14N4O3S2/c17-10(16-19)3-1-2-4-13-1...                     [CHEMBL3287021, CHEMBL3287021]   
InChI=1S/C12H14N4O3S2/c17-9(16-19)3-1-2-4-13-10...                     [CHEMBL3287023, CHEMBL3287023]   
InChI=1S/C12H14O2S3/c1-3-16-12(15)17-8-11(13)9-...                       [CHEMBL242039, CHEMBL242039]   
InChI=1S/C12H15NO3/c14-11(10-6-2-1-3-7-10)8-4-5...            [CHEMBL95152, CHEMBL95152, CHEMBL95152]   
InChI=1S/C12H17NO3S/c14-10(11-7-5-9-17-11)6-3-1...                         [CHEMBL99394, CHEMBL99394]   
InChI=1S/C13H11Br4N7O2/c14-8-9(15)11(17)13-12(1...                     [CHEMBL5191682, CHEMBL5191682]   
InChI=1S/C13H11Cl2N3O4/c14-9-2-1-7(5-10(9)15)12...  [CHEMBL4469488, CHEMBL4469488, CHEMBL4469488, ...   
InChI=1S/C13H12F3N3O3/c1-7(6-20)17-11(21)9-4-2-...                     [CHEMBL3688166, CHEMBL3692586]   
InChI=1S/C13H12N2O/c1-8-13-11(5-6-14-8)10-4-3-9...         [CHEMBL269538, CHEMBL269538, CHEMBL269538]   
InChI=1S/C13H12N2O4S/c16-13(14-17)10-6-8-11(9-7...                         [CHEMBL98345, CHEMBL98345]   
InChI=1S/C13H14N4O2/c1-9(10-5-3-2-4-6-10)16-13-...  [CHEMBL3655915, CHEMBL3655943, CHEMBL3655944, ...   
InChI=1S/C13H16BrN3O5/c14-9-6-8(3-4-11(9)18)7-1...                     [CHEMBL2047685, CHEMBL2047685]   
InChI=1S/C13H16N2O2S/c1-2-13-14-11(10-18-13)8-6...                     [CHEMBL5181798, CHEMBL5186798]   
InChI=1S/C13H16N4O3S2/c1-8-10(16-13(22-8)12-15-...                     [CHEMBL3287251, CHEMBL3287251]   
InChI=1S/C13H16N4O3S2/c1-8-15-10(7-21-8)13-16-9...                     [CHEMBL3287022, CHEMBL3287022]   
InChI=1S/C13H17NO3/c15-12(11-7-3-1-4-8-11)9-5-2...            [CHEMBL95916, CHEMBL95916, CHEMBL95916]   
InChI=1S/C13H17NO4/c15-13(14-16)5-3-1-2-4-10-6-...                     [CHEMBL3890846, CHEMBL3890846]   
InChI=1S/C13H18N2O3/c16-12(11-6-5-9-14-10-11)7-...            [CHEMBL98911, CHEMBL98911, CHEMBL98911]   
InChI=1S/C13H19NOS/c15-13(10-6-1-2-7-11-16)14-1...         [CHEMBL325676, CHEMBL325676, CHEMBL325676]   
InChI=1S/C13H7F3N2O4S3/c14-13(15,16)11(19)7-3-4...                       [CHEMBL471174, CHEMBL471174]   
InChI=1S/C14H13F3N4O2/c15-14(16,17)13-20-11(21-...      [CHEMBL3692616, CHEMBL3692616, CHEMBL3692616]   
InChI=1S/C14H13N3O3/c1-20-13-8-6-12(7-9-13)16-1...                     [CHEMBL5422313, CHEMBL5422313]   
InChI=1S/C14H13N3O3/c18-13(8-10-4-2-1-3-5-10)16...                     [CHEMBL4435005, CHEMBL4435005]   
InChI=1S/C14H14N2O4S/c17-14(15-18)10-11-6-8-12(...                       [CHEMBL319248, CHEMBL319248]   
InChI=1S/C14H14N4O2/c19-12(18-20)10-8-15-13(16-...  [CHEMBL3655950, CHEMBL3655950, CHEMBL3655950, ...   
InChI=1S/C14H15N3O3/c1-17-8-2-3-12(17)14(19)15-...                     [CHEMBL2431862, CHEMBL2431862]   
InChI=1S/C14H16N4O3S2/c1-2-9-11(17-14(23-9)13-1...      [CHEMBL3287267, CHEMBL3287267, CHEMBL3287267]   
InChI=1S/C14H17Cl2N3O4/c15-9-5-4-6-10(16)12(9)1...                     [CHEMBL1085051, CHEMBL1085051]   
InCh

In [82]:
dupl_new = dupl.reset_index()

In [83]:
dupl_new

INCHI  \
0    InChI=1S/C10H7F3N2O4S2/c1-21(17,18)4-7-14-9(19...   
1    InChI=1S/C11H10N4O/c12-8-3-1-2-4-9(8)15-11(16)...   
2    InChI=1S/C11H13BrN2O3S/c12-8-5-7(1-2-10(8)15)6...   
3    InChI=1S/C11H15BrN2O/c1-2-3-8-13-14-11(15)9-4-...   
4    InChI=1S/C11H15BrN2O2S/c12-11-13-9(8-17-11)6-4...   
5    InChI=1S/C12H10F3N3O3/c13-12(14,15)11-17-9(18-...   
6    InChI=1S/C12H11F3N2O4S2/c1-2-5-23(19,20)6-9-16...   
7    InChI=1S/C12H11N3O/c13-10-5-1-2-6-11(10)15-12(...   
8    InChI=1S/C12H14BrN3O5/c13-8-5-7(1-2-10(8)17)6-...   
9    InChI=1S/C12H14N4O3S2/c17-10(16-19)3-1-2-4-13-...   
10   InChI=1S/C12H14N4O3S2/c17-9(16-19)3-1-2-4-13-1...   
11   InChI=1S/C12H14O2S3/c1-3-16-12(15)17-8-11(13)9...   
12   InChI=1S/C12H15NO3/c14-11(10-6-2-1-3-7-10)8-4-...   
13   InChI=1S/C12H17NO3S/c14-10(11-7-5-9-17-11)6-3-...   
14   InChI=1S/C13H11Br4N7O2/c14-8-9(15)11(17)13-12(...   
15   InChI=1S/C13H11Cl2N3O4/c14-9-2-1-7(5-10(9)15)1...   
16   InChI=1S/C13H12F3N3O3/c1-7(6-20)17-11(21)9-4-2...   
17   InChI=1S/C13H12N2O/c1-8-13-11(5-6-14-8)10-4-3-...   
18   InChI=1S/C13H12N2O4S/c16-13(14-17)10-6-8-11(9-...   
19   InChI=1S/C13H14N4O2/c1-9(10-5-3-2-4-6-10)16-13...   
20   InChI=1S/C13H16BrN3O5/c14-9-6-8(3-4-11(9)18)7-...   
21   InChI=1S/C13H16N2O2S/c1-2-13-14-11(10-18-13)8-...   
22   InChI=1S/C13H16N4O3S2/c1-8-10(16-13(22-8)12-15...   
23   InChI=1S/C13H16N4O3S2/c1-8-15-10(7-21-8)13-16-...   
24   InChI=1S/C13H17NO3/c15-12(11-7-3-1-4-8-11)9-5-...   
25   InChI=1S/C13H17NO4/c15-13(14-16)5-3-1-2-4-10-6...   
26   InChI=1S/C13H18N2O3/c16-12(11-6-5-9-14-10-11)7...   
27   InChI=1S/C13H19NOS/c15-13(10-6-1-2-7-11-16)14-...   
28   InChI=1S/C13H7F3N2O4S3/c14-13(15,16)11(19)7-3-...   
29   InChI=1S/C14H13F3N4O2/c15-14(16,17)13-20-11(21...   
30   InChI=1S/C14H13N3O3/c1-20-13-8-6-12(7-9-13)16-...   
31   InChI=1S/C14H13N3O3/c18-13(8-10-4-2-1-3-5-10)1...   
32   InChI=1S/C14H14N2O4S/c17-14(15-18)10-11-6-8-12...   
33   InChI=1S/C14H14N4O2/c19-12(18-20)10-8-15-13(16...   
34   InChI=1S/C14H15N3O3/c1-17-8-2-3-12(17)14(19)15...   
35   InChI=1S/C14H16N4O3S2/c1-2-9-11(17-14(23-9)13-...   
36   InChI=1S/C14H17Cl2N3O4/c15-9-5-4-6-10(16)12(9)...   
37   InChI=1S/C14H17N3O7S/c18-12(15-19)9-5-2-6-10-2...   
38   InChI=1S/C14H18BrN3O4/c15-11-6-4-5-10(9-11)13(...   
39   InChI=1S/C14H18BrN3O4/c15-11-7-5-10(6-8-11)13(...   
40   InChI=1S/C14H18BrNO3/c15-12-9-7-11(8-10-12)13(...   
41   InChI=1S/C14H18ClN3O4/c15-11-7-5-10(6-8-11)13(...   
42   InChI=1S/C14H18FN3O4/c15-11-7-5-10(6-8-11)13(2...   
43   InChI=1S/C14H18IN3O4/c15-11-7-5-10(6-8-11)13(2...   
44   InChI=1S/C14H18N4O3S2/c1-2-9-11(17-14(23-9)13-...   
45   InChI=1S/C14H18N4O6/c19-12(17-22)4-2-1-3-9-15-...   
46   InChI=1S/C14H18N4O6/c19-12(17-22)7-2-1-3-8-15-...   
47   InChI=1S/C14H19ClN4O4/c15-10-6-5-9(8-11(10)16)...   
48   InChI=1S/C14H19N3O4/c18-12(17-21)9-5-2-6-10-15...   
49   InChI=1S/C14H19NO3/c1-18-9-12-3-2-4-13(12)10-5...   
50   InChI=1S/C14H19NO3/c16-13(12-8-4-3-5-9-12)10-6...   
51   InChI=1S/C14H19NO4/c1-19-12-9-7-11(8-10-12)13(...   
52   InChI=1S/C14H20N2O3/c1-19-10-13-3-2-8-16(13)9-...   
53   InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...   
54   InChI=1S/C14H22N2O2/c17-14(16-18)10-6-1-2-7-11...   
55   InChI=1S/C15H10F3NO2S/c16-15(17,18)13(20)11-5-...   
56   InChI=1S/C15H11F2NO2S/c16-14(17)13(19)11-5-6-1...   
57   InChI=1S/C15H12Cl2N2O3/c16-12-6-5-11(7-13(12)1...   
58   InChI=1S/C15H12Cl2N2O4S/c16-11-4-7-14(13(17)9-...   
59   InChI=1S/C15H12Cl2N2O4S/c16-13-7-6-12(9-14(13)...   
60   InChI=1S/C15H12F3NO2S/c1-19(9-10-5-3-2-4-6-10)...   
61   InChI=1S/C15H12F3NO2S/c1-9(10-5-3-2-4-6-10)19-...   
62   InChI=1S/C15H13ClN2O4S/c16-12-4-8-14(9-5-12)23...   
63   InChI=1S/C15H13N3O6S/c19-15(16-20)10-3-11-1-4-...   
64   InChI=1S/C15H14FN3O2/c1-9(20)18-12-5-2-10(3-6-...   
65   InChI=1S/C15H14N2O4S/c18-15(16-19)10-9-12-5-4-...   
66   InChI=1S/C15H14N2O4S/c18-15(16-19)11-8-12-6-9-...   
67   InChI=1S/C15H15N3O2/c1-10(19)17-12-8-6-11(7-9-...   
68   InChI=1S/C15H15N3O3S/c1-9-7-14(21)18-15(16

In [84]:
dupl_new['pAct mean'] = [np.mean(i) for i in dupl_new['pAct']]
# calcolo la std dei duplicati stereo
dupl_new['pAct std'] = [np.std(i) for i in dupl_new['pAct']] #standard deviation
dupl_new.head()


INCHI  \
0  InChI=1S/C10H7F3N2O4S2/c1-21(17,18)4-7-14-9(19...   
1  InChI=1S/C11H10N4O/c12-8-3-1-2-4-9(8)15-11(16)...   
2  InChI=1S/C11H13BrN2O3S/c12-8-5-7(1-2-10(8)15)6...   
3  InChI=1S/C11H15BrN2O/c1-2-3-8-13-14-11(15)9-4-...   
4  InChI=1S/C11H15BrN2O2S/c12-11-13-9(8-17-11)6-4...   

                                              ID  \
0                   [CHEMBL512516, CHEMBL512516]   
1  [CHEMBL4283263, CHEMBL4283263, CHEMBL4283263]   
2                 [CHEMBL2047540, CHEMBL2047540]   
3  [CHEMBL4303643, CHEMBL4303643, CHEMBL4303643]   
4                 [CHEMBL5193020, CHEMBL5174162]   

                                     ISOMERIC SMILES  \
0  [CS(=O)(=O)Cc1noc(-c2ccc(C(=O)C(F)(F)F)s2)n1, ...   
1  [Nc1ccccc1NC(=O)c1cnccn1, Nc1ccccc1NC(=O)c1cnc...   
2  [O=C(NCCS)/C(Cc1ccc(O)c(Br)c1)=N/O, O=C(NCCS)/...   
3  [CCCCNNC(=O)c1ccc(Br)cc1, CCCCNNC(=O)c1ccc(Br)...   
4  [O=C(CCCCC/C=C\c1csc(Br)n1)NO, O=C(CCCCC/C=C/c...   

                                                pAct  \
0             [5.607303046740334, 5.568636235841013]   
1  [5.637894680706227, 5.637894680706227, 5.69897...   
2            [9.045757490560675, 7.2839966563652006]   
3  [6.301029995663981, 5.847711655616943, 6.30102...   
4             [6.537602002101044, 6.769551078621726]   

                                  ISOMERIC MOLECULES Configuration  \
0  [<rdkit.Chem.rdchem.Mol object at 0x7f00cd0d05...      [[], []]   
1  [<rdkit.Chem.rdchem.Mol object at 0x7f00cd0d09...  [[], [], []]   
2  [<rdkit.Chem.rdchem.Mol object at 0x7f00cd0d0e...      [[], []]   
3  [<rdkit.Chem.rdchem.Mol object at 0x7f00cd0d01...  [[], [], []]   
4  [<rdkit.Chem.rdchem.Mol object at 0x7f00cd0d0c...      [[], []]   

  STANDARD RELATION  pAct mean  pAct std  
0        ['=', '=']   5.587970  0.019333  
1   ['=', '=', '=']   5.658253  0.028791  
2        ['=', '=']   8.164877  0.880880  
3   ['=', '=', '=']   6.149924  0.213696  
4        ['=', '=']   6.653577  0.115975

In [85]:
dupl_ok = dupl_new[dupl_new['pAct std'] <= 1]

In [86]:
dupl_ok

INCHI  \
0    InChI=1S/C10H7F3N2O4S2/c1-21(17,18)4-7-14-9(19...   
1    InChI=1S/C11H10N4O/c12-8-3-1-2-4-9(8)15-11(16)...   
2    InChI=1S/C11H13BrN2O3S/c12-8-5-7(1-2-10(8)15)6...   
3    InChI=1S/C11H15BrN2O/c1-2-3-8-13-14-11(15)9-4-...   
4    InChI=1S/C11H15BrN2O2S/c12-11-13-9(8-17-11)6-4...   
5    InChI=1S/C12H10F3N3O3/c13-12(14,15)11-17-9(18-...   
6    InChI=1S/C12H11F3N2O4S2/c1-2-5-23(19,20)6-9-16...   
7    InChI=1S/C12H11N3O/c13-10-5-1-2-6-11(10)15-12(...   
8    InChI=1S/C12H14BrN3O5/c13-8-5-7(1-2-10(8)17)6-...   
9    InChI=1S/C12H14N4O3S2/c17-10(16-19)3-1-2-4-13-...   
10   InChI=1S/C12H14N4O3S2/c17-9(16-19)3-1-2-4-13-1...   
11   InChI=1S/C12H14O2S3/c1-3-16-12(15)17-8-11(13)9...   
12   InChI=1S/C12H15NO3/c14-11(10-6-2-1-3-7-10)8-4-...   
13   InChI=1S/C12H17NO3S/c14-10(11-7-5-9-17-11)6-3-...   
14   InChI=1S/C13H11Br4N7O2/c14-8-9(15)11(17)13-12(...   
15   InChI=1S/C13H11Cl2N3O4/c14-9-2-1-7(5-10(9)15)1...   
16   InChI=1S/C13H12F3N3O3/c1-7(6-20)17-11(21)9-4-2...   
17   InChI=1S/C13H12N2O/c1-8-13-11(5-6-14-8)10-4-3-...   
18   InChI=1S/C13H12N2O4S/c16-13(14-17)10-6-8-11(9-...   
19   InChI=1S/C13H14N4O2/c1-9(10-5-3-2-4-6-10)16-13...   
20   InChI=1S/C13H16BrN3O5/c14-9-6-8(3-4-11(9)18)7-...   
21   InChI=1S/C13H16N2O2S/c1-2-13-14-11(10-18-13)8-...   
22   InChI=1S/C13H16N4O3S2/c1-8-10(16-13(22-8)12-15...   
23   InChI=1S/C13H16N4O3S2/c1-8-15-10(7-21-8)13-16-...   
24   InChI=1S/C13H17NO3/c15-12(11-7-3-1-4-8-11)9-5-...   
25   InChI=1S/C13H17NO4/c15-13(14-16)5-3-1-2-4-10-6...   
26   InChI=1S/C13H18N2O3/c16-12(11-6-5-9-14-10-11)7...   
27   InChI=1S/C13H19NOS/c15-13(10-6-1-2-7-11-16)14-...   
28   InChI=1S/C13H7F3N2O4S3/c14-13(15,16)11(19)7-3-...   
29   InChI=1S/C14H13F3N4O2/c15-14(16,17)13-20-11(21...   
30   InChI=1S/C14H13N3O3/c1-20-13-8-6-12(7-9-13)16-...   
31   InChI=1S/C14H13N3O3/c18-13(8-10-4-2-1-3-5-10)1...   
32   InChI=1S/C14H14N2O4S/c17-14(15-18)10-11-6-8-12...   
33   InChI=1S/C14H14N4O2/c19-12(18-20)10-8-15-13(16...   
34   InChI=1S/C14H15N3O3/c1-17-8-2-3-12(17)14(19)15...   
35   InChI=1S/C14H16N4O3S2/c1-2-9-11(17-14(23-9)13-...   
36   InChI=1S/C14H17Cl2N3O4/c15-9-5-4-6-10(16)12(9)...   
38   InChI=1S/C14H18BrN3O4/c15-11-6-4-5-10(9-11)13(...   
39   InChI=1S/C14H18BrN3O4/c15-11-7-5-10(6-8-11)13(...   
40   InChI=1S/C14H18BrNO3/c15-12-9-7-11(8-10-12)13(...   
41   InChI=1S/C14H18ClN3O4/c15-11-7-5-10(6-8-11)13(...   
42   InChI=1S/C14H18FN3O4/c15-11-7-5-10(6-8-11)13(2...   
44   InChI=1S/C14H18N4O3S2/c1-2-9-11(17-14(23-9)13-...   
45   InChI=1S/C14H18N4O6/c19-12(17-22)4-2-1-3-9-15-...   
46   InChI=1S/C14H18N4O6/c19-12(17-22)7-2-1-3-8-15-...   
48   InChI=1S/C14H19N3O4/c18-12(17-21)9-5-2-6-10-15...   
49   InChI=1S/C14H19NO3/c1-18-9-12-3-2-4-13(12)10-5...   
50   InChI=1S/C14H19NO3/c16-13(12-8-4-3-5-9-12)10-6...   
51   InChI=1S/C14H19NO4/c1-19-12-9-7-11(8-10-12)13(...   
52   InChI=1S/C14H20N2O3/c1-19-10-13-3-2-8-16(13)9-...   
53   InChI=1S/C14H20N2O3/c17-13(15-12-8-4-3-5-9-12)...   
54   InChI=1S/C14H22N2O2/c17-14(16-18)10-6-1-2-7-11...   
55   InChI=1S/C15H10F3NO2S/c16-15(17,18)13(20)11-5-...   
56   InChI=1S/C15H11F2NO2S/c16-14(17)13(19)11-5-6-1...   
57   InChI=1S/C15H12Cl2N2O3/c16-12-6-5-11(7-13(12)1...   
58   InChI=1S/C15H12Cl2N2O4S/c16-11-4-7-14(13(17)9-...   
59   InChI=1S/C15H12Cl2N2O4S/c16-13-7-6-12(9-14(13)...   
60   InChI=1S/C15H12F3NO2S/c1-19(9-10-5-3-2-4-6-10)...   
61   InChI=1S/C15H12F3NO2S/c1-9(10-5-3-2-4-6-10)19-...   
62   InChI=1S/C15H13ClN2O4S/c16-12-4-8-14(9-5-12)23...   
63   InChI=1S/C15H13N3O6S/c19-15(16-20)10-3-11-1-4-...   
64   InChI=1S/C15H14FN3O2/c1-9(20)18-12-5-2-10(3-6-...   
65   InChI=1S/C15H14N2O4S/c18-15(16-19)10-9-12-5-4-...   
66   InChI=1S/C15H14N2O4S/c18-15(16-19)11-8-12-6-9-...   
67   InChI=1S/C15H15N3O2/c1-10(19)17-12-8-6-11(7-9-...   
68   InChI=1S/C15H15N3O3S/c1-9-7-14(21)18-15(16-9)2...   
69   InChI=1S/C15H15N3O6S2/c16-25(21,22)13-6-8-14(9...   
70   InChI=1S/C15H16N2O2S/c18-14(17-19)8-4-7-13-11-...   
71   InChI=1S/C15H16N2O4S/c18-15(16-19)11-8-12-

In [87]:
dupl_ok_bis = copy.deepcopy(dupl_ok)
dupl_ok_bis['ID'] = [i[0] for i in dupl_ok['ID']]
dupl_ok_bis['ISOMERIC SMILES'] = [i[0] for i in dupl_ok['ISOMERIC SMILES']]

In [88]:
dupl_ok_bis = dupl_ok_bis[['ID', 'INCHI', 'ISOMERIC SMILES', 'STANDARD RELATION', 'pAct mean']]

In [89]:
dupl_ok_bis['pAct'] = dupl_ok_bis['pAct mean']

In [90]:
dupl_ok_bis.drop(columns=['pAct mean'], inplace=True)

In [91]:
df.columns

Index(['ID', 'INCHI', 'ISOMERIC SMILES', 'CANONICAL SMILES',
       'STANDARD RELATION', 'STANDARD VALUE [nM]', 'pAct'],
      dtype='object')

In [92]:
df.drop(columns=['CANONICAL SMILES','STANDARD VALUE [nM]'], inplace=True)

/tmp/ipykernel_574748/999636266.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.drop(columns=['CANONICAL SMILES','STANDARD VALUE [nM]'], inplace=True)


In [93]:
df_unito = pd.concat([df, dupl_ok_bis], ignore_index=True)

In [94]:
df_unito.shape

(6696, 5)

In [95]:
df_unito.index

RangeIndex(start=0, stop=6696, step=1)

In [97]:
df_unito.head()

ID                                              INCHI  \
0  CHEMBL3936525  InChI=1S/C19H22FN3O2/c20-15-9-4-3-8-14(15)19(2...   
1   CHEMBL327924  InChI=1S/C20H22N4O3/c21-15-9-4-6-11-17(15)22-1...   
2  CHEMBL2442802  InChI=1S/C34H38N2O10/c1-41-27-13-19(14-28(42-2...   
3  CHEMBL2442794  InChI=1S/C32H34N2O10/c1-39-25-11-17(12-26(40-2...   
4  CHEMBL2442792  InChI=1S/C31H32N2O10/c1-38-24-9-16(10-25(39-2)...   

                                     ISOMERIC SMILES STANDARD RELATION  \
0                Nc1ccccc1NC(=O)CCCCCNC(=O)c1ccccc1F               '='   
1        Nc1ccccc1NC(=O)CCCCCn1c(=O)[nH]c2ccccc2c1=O               '='   
2  COc1cc([C@@H]2c3cc4c(cc3[C@@H](Nc3ccccc3OCCCCC...               '='   
3  COc1cc([C@@H]2c3cc4c(cc3[C@@H](Nc3ccc(OCCCCC(=...               '='   
4  COc1cc([C@@H]2c3cc4c(cc3[C@@H](Nc3cccc(OCCCC(=...               '='   

       pAct  
0  5.945004  
1  5.397940  
2  7.142668  
3  6.903090  
4  6.414539

In [98]:
#all_df['INCHI'] = [i.strip('\n') for i in all_df['INCHI'].values] #serve per levare \n alla fine dell'inchi GIÀ LEVATI

In [99]:
#inserimento colonne strutture molecolari
PandasTools.AddMoleculeColumnToFrame(frame=df_unito, smilesCol='ISOMERIC SMILES', molCol='ISOMERIC MOLECULES') 

In [100]:
df_unito['MW'] = [Chem.Descriptors.ExactMolWt(Chem.MolFromSmiles(i)) for i in df_unito['ISOMERIC SMILES']]#LO RICALCOLO CORRETTO PRIMA C'ERANO IONI

In [101]:
df_unito.shape

(6696, 7)

In [102]:
len(set(list(df_unito['ISOMERIC SMILES'])))# questopiù duplicati conferma che non ho

6696

In [103]:
df_unito.index

RangeIndex(start=0, stop=6696, step=1)

# 13. SELEZIONE PER PESO MOLECOLARE


In [104]:
final_df = df_unito

In [105]:
final_df['MW'].describe()

count    6696.000000
mean      429.564968
std       118.112056
min        87.045153
25%       354.132194
50%       412.189926
75%       487.063448
max      1597.743947
Name: MW, dtype: float64

In [106]:
final_df.shape

(6696, 7)

In [107]:
final_df = final_df.reset_index(drop=True)

In [108]:
final_df.head()

ID                                              INCHI  \
0  CHEMBL3936525  InChI=1S/C19H22FN3O2/c20-15-9-4-3-8-14(15)19(2...   
1   CHEMBL327924  InChI=1S/C20H22N4O3/c21-15-9-4-6-11-17(15)22-1...   
2  CHEMBL2442802  InChI=1S/C34H38N2O10/c1-41-27-13-19(14-28(42-2...   
3  CHEMBL2442794  InChI=1S/C32H34N2O10/c1-39-25-11-17(12-26(40-2...   
4  CHEMBL2442792  InChI=1S/C31H32N2O10/c1-38-24-9-16(10-25(39-2)...   

                                     ISOMERIC SMILES STANDARD RELATION  \
0                Nc1ccccc1NC(=O)CCCCCNC(=O)c1ccccc1F               '='   
1        Nc1ccccc1NC(=O)CCCCCn1c(=O)[nH]c2ccccc2c1=O               '='   
2  COc1cc([C@@H]2c3cc4c(cc3[C@@H](Nc3ccccc3OCCCCC...               '='   
3  COc1cc([C@@H]2c3cc4c(cc3[C@@H](Nc3ccc(OCCCCC(=...               '='   
4  COc1cc([C@@H]2c3cc4c(cc3[C@@H](Nc3cccc(OCCCC(=...               '='   

       pAct                                ISOMERIC MOLECULES          MW  
0  5.945004  <rdkit.Chem.rdchem.Mol object at 0x7f00cbf829d0>  343.169605  
1  5.397940  <rdkit.Chem.rdchem.Mol object at 0x7f00cbf82810>  366.169191  
2  7.142668  <rdkit.Chem.rdchem.Mol object at 0x7f00cbf82730>  634.252645  
3  6.903090  <rdkit.Chem.rdchem.Mol object at 0x7f00cbf82a40>  606.221345  
4  6.414539  <rdkit.Chem.rdchem.Mol object at 0x7f00cbf82960>  592.205695

In [109]:
name = f'CLEANED_{purpose}_ChEMBL_{std_type}_{len(final_df)}.pkl'

In [110]:
name

'CLEANED_CLASSIFICATION_ChEMBL_IC50_6696.pkl'

In [111]:
path = '/home/robertastolfi/HDAC/HDAC1'

In [112]:
path 

'/home/robertastolfi/HDAC/HDAC1'

In [113]:
with open(f'{path}/{name}', 'wb') as fp:
     pickle.dump(final_df, fp)